In [144]:
import pandas as pd

# 读取四个CSV文件
games_simlified = pd.read_csv('games_simplified.csv')
price_data = pd.read_csv('price_final.csv')  
player_count_data = pd.read_csv('count_final.csv')  
review_count_data = pd.read_csv('review_final.csv')  

# 查看每个数据集的基本信息
def print_data_info(df, name):
    print(f"Dataset: {name}")
    print(f"Shape: {df.shape}")
    print(f"Columns: {df.columns.tolist()}")
    print(f"Data Types: {df.dtypes}")
    print(f"Missing Values: {df.isnull().sum()}")
    print("\nSample Data:")
    print(df.head(), "\n\n")

# 输出每个数据集的信息
print_data_info(games_simlified, "games_simlified")
print_data_info(price_data, "price")
print_data_info(player_count_data, "count")
print_data_info(review_count_data, "review")

Dataset: games_simlified
Shape: (111452, 26)
Columns: ['AppID', 'Name', 'Release date', 'Estimated owners', 'Peak CCU', 'Price', 'Discount', 'DLC count', 'Windows', 'Mac', 'Linux', 'Metacritic score', 'User score', 'Positive', 'Negative', 'Achievements', 'Recommendations', 'Average playtime forever', 'Average playtime two weeks', 'Median playtime forever', 'Median playtime two weeks', 'Developers', 'Publishers', 'Categories', 'Genres', 'Tags']
Data Types: AppID                           int64
Name                           object
Release date                   object
Estimated owners               object
Peak CCU                        int64
Price                         float64
Discount                        int64
DLC count                       int64
Windows                          bool
Mac                              bool
Linux                            bool
Metacritic score                int64
User score                      int64
Positive                        int64
Negative

# 第一阶段：初步数据探索

## 目标
1. 了解游戏数量的时间分布（发行趋势）
2. 探索价格分布和定价策略
3. 分析玩家规模分布（estimated owners, peak CCU）
4. 查看评价分布（positive vs negative）
5. 研究不同类型（genres）和标签（tags）的分布

In [145]:
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np
from datetime import datetime
import pandas as pd

# 数据预处理
# 1. 处理Release date - 转换为datetime格式
games_simlified['Release date'] = pd.to_datetime(games_simlified['Release date'], errors='coerce')
games_simlified['Release year'] = games_simlified['Release date'].dt.year
games_simlified['Release month'] = games_simlified['Release date'].dt.to_period('M')

# 2. 处理Estimated owners - 提取范围的中位数
def parse_owners(owner_str):
    if pd.isna(owner_str):
        return np.nan
    try:
        # 格式: "0 - 20000" 或 "20000 - 50000"
        parts = owner_str.split(' - ')
        if len(parts) == 2:
            low = int(parts[0].replace(',', ''))
            high = int(parts[1].replace(',', ''))
            return (low + high) / 2
    except:
        return np.nan
    return np.nan

games_simlified['Estimated owners (mid)'] = games_simlified['Estimated owners'].apply(parse_owners)

# 3. 计算正面评价率
games_simlified['Positive rate'] = games_simlified['Positive'] / (games_simlified['Positive'] + games_simlified['Negative'])
games_simlified['Positive rate'] = games_simlified['Positive rate'].fillna(0)

# 4. 计算总评价数
games_simlified['Total reviews'] = games_simlified['Positive'] + games_simlified['Negative']

print("数据预处理完成！")
print(f"Release year 范围: {games_simlified['Release year'].min()} - {games_simlified['Release year'].max()}")
print(f"Estimated owners (mid) 范围: {games_simlified['Estimated owners (mid)'].min():.0f} - {games_simlified['Estimated owners (mid)'].max():.0f}")
print(f"价格范围: ${games_simlified['Price'].min()} - ${games_simlified['Price'].max()}")
print(f"总评价数范围: {games_simlified['Total reviews'].min()} - {games_simlified['Total reviews'].max()}")

数据预处理完成！
Release year 范围: 1997.0 - 2025.0
Estimated owners (mid) 范围: 0 - 150000000
价格范围: $0.0 - $999.98
总评价数范围: 0 - 6531097


## 1. 游戏发行趋势分析

In [146]:
# 每年发行的游戏数量
yearly_releases = games_simlified.groupby('Release year').size().reset_index(name='Count')
yearly_releases = yearly_releases[yearly_releases['Release year'].notna()]

fig1 = px.line(yearly_releases, 
               x='Release year', 
               y='Count',
               title='Steam游戏年度发行数量趋势 (2008-2024)',
               labels={'Release year': '年份', 'Count': '发行游戏数量'},
               markers=True)

fig1.update_layout(
    height=400,
    hovermode='x unified'
)

fig1.show()

# 输出关键统计
print(f"数据覆盖年份: {yearly_releases['Release year'].min():.0f} - {yearly_releases['Release year'].max():.0f}")
print(f"发行数量最多的年份: {yearly_releases.loc[yearly_releases['Count'].idxmax(), 'Release year']:.0f} ({yearly_releases['Count'].max()}款游戏)")
print(f"平均每年发行: {yearly_releases['Count'].mean():.0f}款游戏")

数据覆盖年份: 1997 - 2025
发行数量最多的年份: 2024 (20583款游戏)
平均每年发行: 3839款游戏


## 2. 价格分布分析

In [147]:
# 价格分布分析
# 创建价格区间
def price_category(price):
    if price == 0:
        return '免费'
    elif price < 5:
        return '$0-5'
    elif price < 10:
        return '$5-10'
    elif price < 20:
        return '$10-20'
    elif price < 30:
        return '$20-30'
    elif price < 50:
        return '$30-50'
    else:
        return '$50+'

games_simlified['Price category'] = games_simlified['Price'].apply(price_category)

# 统计每个价格区间的游戏数量
price_dist = games_simlified['Price category'].value_counts().reset_index()
price_dist.columns = ['Price category', 'Count']

# 按照价格顺序排列
category_order = ['免费', '$0-5', '$5-10', '$10-20', '$20-30', '$30-50', '$50+']
price_dist['Price category'] = pd.Categorical(price_dist['Price category'], categories=category_order, ordered=True)
price_dist = price_dist.sort_values('Price category')

fig2 = px.bar(price_dist,
              x='Price category',
              y='Count',
              title='Steam游戏价格分布',
              labels={'Price category': '价格区间', 'Count': '游戏数量'},
              text='Count')

fig2.update_traces(texttemplate='%{text}', textposition='outside')
fig2.update_layout(height=400)
fig2.show()

# 输出关键统计
print(f"免费游戏数量: {games_simlified[games_simlified['Price'] == 0].shape[0]} ({games_simlified[games_simlified['Price'] == 0].shape[0]/len(games_simlified)*100:.1f}%)")
print(f"付费游戏数量: {games_simlified[games_simlified['Price'] > 0].shape[0]} ({games_simlified[games_simlified['Price'] > 0].shape[0]/len(games_simlified)*100:.1f}%)")
print(f"付费游戏平均价格: ${games_simlified[games_simlified['Price'] > 0]['Price'].mean():.2f}")
print(f"付费游戏中位数价格: ${games_simlified[games_simlified['Price'] > 0]['Price'].median():.2f}")

免费游戏数量: 23247 (20.9%)
付费游戏数量: 88205 (79.1%)
付费游戏平均价格: $8.92
付费游戏中位数价格: $5.09


## 3. 玩家规模与市场表现

In [148]:
# 玩家规模分析 - 使用散点图查看价格与玩家数量的关系
# 过滤掉异常值，只看有足够数据的游戏
games_filtered = games_simlified[
    (games_simlified['Total reviews'] >= 10) &  # 至少10个评价
    (games_simlified['Estimated owners (mid)'] > 0) &  # 有拥有者数据
    (games_simlified['Peak CCU'] > 0)  # 有在线峰值数据
].copy()

print(f"筛选后的游戏数量: {len(games_filtered)} (占总数的 {len(games_filtered)/len(games_simlified)*100:.1f}%)")

# 创建散点图：价格 vs 估计拥有者数量
fig3 = px.scatter(games_filtered.sample(min(5000, len(games_filtered))),  # 采样避免过多数据点
                  x='Price',
                  y='Estimated owners (mid)',
                  color='Positive rate',
                  size='Peak CCU',
                  hover_data=['Name', 'Total reviews'],
                  title='价格 vs 拥有者数量 (气泡大小=峰值在线人数，颜色=好评率)',
                  labels={
                      'Price': '价格 ($)',
                      'Estimated owners (mid)': '估计拥有者数量',
                      'Positive rate': '好评率'
                  },
                  color_continuous_scale='RdYlGn',
                  range_color=[0, 1])

fig3.update_layout(height=500)
fig3.show()

# 按价格区间统计平均表现
price_performance = games_filtered.groupby('Price category').agg({
    'Estimated owners (mid)': 'mean',
    'Peak CCU': 'mean',
    'Positive rate': 'mean',
    'Total reviews': 'mean',
    'AppID': 'count'
}).reset_index()
price_performance.columns = ['Price category', 'Avg owners', 'Avg peak CCU', 'Avg positive rate', 'Avg reviews', 'Game count']

# 按照价格顺序排列
price_performance['Price category'] = pd.Categorical(price_performance['Price category'], 
                                                      categories=category_order, ordered=True)
price_performance = price_performance.sort_values('Price category')

print("\n各价格区间的平均表现:")
print(price_performance.to_string(index=False))

筛选后的游戏数量: 21218 (占总数的 19.0%)



各价格区间的平均表现:
Price category    Avg owners  Avg peak CCU  Avg positive rate  Avg reviews  Game count
            免费 963670.009551   1606.108883           0.763415 12630.208214        2094
          $0-5 133898.471188     70.999804           0.816081  1130.063897        5102
         $5-10 196724.539488    241.413085           0.837430  2548.593267        4723
        $10-20 230225.052058    321.922794           0.839323  3545.440333        6243
        $20-30 333988.261599   2205.452208           0.810330  6447.424818        1789
        $30-50 496333.693305   2384.447084           0.785596  9657.188985         926
          $50+ 965923.753666  19457.926686           0.750189 18375.486804         341


## 4. 评价与玩家粘性分析

In [149]:
# 评价率 vs 平均游戏时长的关系
# 筛选有足够数据的游戏
playtime_filtered = games_filtered[games_filtered['Average playtime forever'] > 0].copy()

fig4 = px.scatter(playtime_filtered.sample(min(5000, len(playtime_filtered))),
                  x='Average playtime forever',
                  y='Positive rate',
                  color='Price category',
                  size='Total reviews',
                  hover_data=['Name', 'Estimated owners (mid)'],
                  title='平均游戏时长 vs 好评率 (气泡大小=总评价数)',
                  labels={
                      'Average playtime forever': '平均游戏时长 (分钟)',
                      'Positive rate': '好评率',
                      'Price category': '价格区间'
                  },
                  category_orders={'Price category': category_order})

fig4.update_xaxes(type='log')  # 使用对数坐标，因为游戏时长差异很大
fig4.update_layout(height=500)
fig4.show()

# 计算相关性
correlation = playtime_filtered[['Average playtime forever', 'Positive rate', 'Total reviews', 'Estimated owners (mid)', 'Peak CCU']].corr()
print("\n关键指标相关性矩阵:")
print(correlation.round(3))


关键指标相关性矩阵:
                          Average playtime forever  Positive rate  \
Average playtime forever                     1.000          0.017   
Positive rate                                0.017          1.000   
Total reviews                                0.210          0.047   
Estimated owners (mid)                       0.216          0.048   
Peak CCU                                     0.105          0.023   

                          Total reviews  Estimated owners (mid)  Peak CCU  
Average playtime forever          0.210                   0.216     0.105  
Positive rate                     0.047                   0.048     0.023  
Total reviews                     1.000                   0.682     0.471  
Estimated owners (mid)            0.682                   1.000     0.467  
Peak CCU                          0.471                   0.467     1.000  


## 5. 游戏类型（Genres）分析

In [150]:
# 解析genres字段（多个genres用逗号分隔）
from collections import Counter

# 提取所有genres
all_genres = []
for genres_str in games_simlified['Genres'].dropna():
    genres_list = [g.strip() for g in str(genres_str).split(',')]
    all_genres.extend(genres_list)

# 统计每个genre的出现次数
genre_counts = Counter(all_genres)
top_genres = pd.DataFrame(genre_counts.most_common(20), columns=['Genre', 'Count'])

fig5 = px.bar(top_genres,
              x='Count',
              y='Genre',
              orientation='h',
              title='Top 20 游戏类型分布',
              labels={'Count': '游戏数量', 'Genre': '游戏类型'},
              text='Count')

fig5.update_traces(texttemplate='%{text}', textposition='outside')
fig5.update_layout(height=600, yaxis={'categoryorder': 'total ascending'})
fig5.show()

print(f"\n总共有 {len(genre_counts)} 种不同的游戏类型")
print(f"前5名游戏类型:")
for i, (genre, count) in enumerate(genre_counts.most_common(5), 1):
    print(f"{i}. {genre}: {count} 款游戏 ({count/len(games_simlified)*100:.1f}%)")


总共有 34 种不同的游戏类型
前5名游戏类型:
1. Indie: 73095 款游戏 (65.6%)
2. Casual: 45115 款游戏 (40.5%)
3. Action: 42654 款游戏 (38.3%)
4. Adventure: 40751 款游戏 (36.6%)
5. Simulation: 21432 款游戏 (19.2%)


In [151]:
# 分析不同游戏类型的市场表现
# 为每个游戏标记主要类型（第一个genre）
games_with_genre = games_filtered.copy()
games_with_genre['Primary genre'] = games_with_genre['Genres'].apply(
    lambda x: str(x).split(',')[0].strip() if pd.notna(x) else 'Unknown'
)

# 只看主要的genres
top_genre_names = [g for g, c in genre_counts.most_common(10)]
genre_performance = games_with_genre[games_with_genre['Primary genre'].isin(top_genre_names)].groupby('Primary genre').agg({
    'Estimated owners (mid)': 'mean',
    'Positive rate': 'mean',
    'Price': 'mean',
    'Peak CCU': 'mean',
    'AppID': 'count'
}).reset_index()

genre_performance.columns = ['Genre', 'Avg owners', 'Avg positive rate', 'Avg price', 'Avg peak CCU', 'Game count']
genre_performance = genre_performance.sort_values('Avg owners', ascending=False)

fig6 = make_subplots(
    rows=2, cols=2,
    subplot_titles=('平均拥有者数量', '平均好评率', '平均价格', '平均峰值在线人数'),
    specs=[[{'type': 'bar'}, {'type': 'bar'}],
           [{'type': 'bar'}, {'type': 'bar'}]]
)

# 添加四个子图
fig6.add_trace(
    go.Bar(x=genre_performance['Genre'], y=genre_performance['Avg owners'], name='Avg owners'),
    row=1, col=1
)

fig6.add_trace(
    go.Bar(x=genre_performance.sort_values('Avg positive rate', ascending=False)['Genre'], 
           y=genre_performance.sort_values('Avg positive rate', ascending=False)['Avg positive rate'], 
           name='Avg positive rate'),
    row=1, col=2
)

fig6.add_trace(
    go.Bar(x=genre_performance.sort_values('Avg price', ascending=False)['Genre'], 
           y=genre_performance.sort_values('Avg price', ascending=False)['Avg price'], 
           name='Avg price'),
    row=2, col=1
)

fig6.add_trace(
    go.Bar(x=genre_performance.sort_values('Avg peak CCU', ascending=False)['Genre'], 
           y=genre_performance.sort_values('Avg peak CCU', ascending=False)['Avg peak CCU'], 
           name='Avg peak CCU'),
    row=2, col=2
)

fig6.update_xaxes(tickangle=45)
fig6.update_layout(height=800, title_text="Top 10游戏类型的市场表现对比", showlegend=False)
fig6.show()

print("\n各游戏类型的详细表现:")
print(genre_performance.to_string(index=False))


各游戏类型的详细表现:
       Genre    Avg owners  Avg positive rate  Avg price  Avg peak CCU  Game count
      Action 507805.427183           0.812099  13.556050   1810.391634        8439
Free to Play 454531.772575           0.738574   0.233712    285.448161         299
    Strategy 357841.796875           0.804834  16.079355    596.070312         512
         RPG 325103.626943           0.806838  20.471917    660.918826         579
  Simulation 229934.036939           0.752330  19.889749   1945.410290         758
      Sports 178389.830508           0.704289  16.441017    146.796610          59
       Indie 157061.994609           0.824536  12.451473    259.623091        2226
   Adventure 134389.030072           0.849904  11.831209    181.003600        4722
      Casual 121813.112538           0.833505   7.307840    165.555255        2959
Early Access 111250.000000           0.895851  14.315000    680.000000           4


## 初步探索总结

请运行以上所有代码单元格，查看可视化结果和统计数据。完成后我们将基于这些发现形成假设并规划下一步分析。

---

# 第二阶段：深入分析 - 为开发者提供定价策略建议

## 任务2.1：计算收入估算并找出收入最优定价策略

在这个阶段，我们将：
1. 创建收入估算列（拥有者数 × 价格）
2. 按游戏类型分析最优定价策略
3. 可视化不同类型游戏的价格-收入关系

In [152]:
# 1. 创建收入估算列
# 收入估算 = 拥有者数量（中位数）× 价格

games_with_genre['Estimated revenue'] = games_with_genre['Estimated owners (mid)'] * games_with_genre['Price']

# 查看收入估算的基本统计
print("收入估算的基本统计:")
print(f"平均收入估算: ${games_with_genre['Estimated revenue'].mean():,.0f}")
print(f"中位数收入估算: ${games_with_genre['Estimated revenue'].median():,.0f}")
print(f"最高收入估算: ${games_with_genre['Estimated revenue'].max():,.0f}")
print(f"最低收入估算: ${games_with_genre['Estimated revenue'].min():,.0f}")

# 找出收入最高的10款游戏
top_revenue_games = games_with_genre.nlargest(10, 'Estimated revenue')[
    ['Name', 'Price', 'Estimated owners (mid)', 'Estimated revenue', 'Primary genre', 'Positive rate']
]

print("\n收入估算最高的10款游戏:")
print(top_revenue_games.to_string(index=False))

收入估算的基本统计:
平均收入估算: $4,353,464
中位数收入估算: $179,900
最高收入估算: $4,499,250,000
最低收入估算: $0

收入估算最高的10款游戏:
                           Name  Price  Estimated owners (mid)  Estimated revenue Primary genre  Positive rate
             Black Myth: Wukong  59.99              75000000.0       4499250000.0        Action       0.958515
                      New World  39.99              75000000.0       2999250000.0        Action       0.677030
                     ELDEN RING  59.99              35000000.0       2099650000.0        Action       0.899936
                           Rust  39.99              35000000.0       1399650000.0        Action       0.866706
                 Cyberpunk 2077  59.99              15000000.0        899850000.0           RPG       0.750895
   Mount & Blade II: Bannerlord  49.99              15000000.0        749850000.0        Action       0.876790
Tom Clancy's Rainbow Six® Siege  19.99              35000000.0        699650000.0        Action       0.870278
               

In [153]:
# 2. 按价格区间分析收入表现
price_revenue_analysis = games_with_genre.groupby('Price category').agg({
    'Estimated revenue': ['mean', 'median', 'sum'],
    'Estimated owners (mid)': 'mean',
    'Price': 'mean',
    'Positive rate': 'mean',
    'AppID': 'count'
}).reset_index()

price_revenue_analysis.columns = ['Price category', 'Avg revenue', 'Median revenue', 'Total revenue', 
                                   'Avg owners', 'Avg price', 'Avg positive rate', 'Game count']

# 按照价格顺序排列
price_revenue_analysis['Price category'] = pd.Categorical(
    price_revenue_analysis['Price category'], 
    categories=category_order, 
    ordered=True
)
price_revenue_analysis = price_revenue_analysis.sort_values('Price category')

print("各价格区间的收入表现分析:")
print(price_revenue_analysis.to_string(index=False))

# 可视化：各价格区间的平均收入
fig7 = px.bar(price_revenue_analysis,
              x='Price category',
              y='Avg revenue',
              title='各价格区间的平均收入估算',
              labels={'Price category': '价格区间', 'Avg revenue': '平均收入估算 ($)'},
              text='Avg revenue')

fig7.update_traces(texttemplate='$%{text:,.0f}', textposition='outside')
fig7.update_layout(height=400)
fig7.show()

各价格区间的收入表现分析:
Price category  Avg revenue  Median revenue  Total revenue    Avg owners  Avg price  Avg positive rate  Game count
            免费 0.000000e+00             0.0   0.000000e+00 963670.009551   0.000000           0.763415        2094
          $0-5 4.633250e+05         49900.0   2.363884e+09 133898.471188   3.172423           0.816081        5102
         $5-10 1.809527e+06         99900.0   8.546395e+09 196724.539488   8.539856           0.837430        4723
        $10-20 4.084597e+06        419650.0   2.550014e+10 230225.052058  16.419286           0.839323        6243
        $20-30 9.469228e+06        979650.0   1.694045e+10 333988.261599  27.032476           0.810330        1789
        $30-50 2.052214e+07       1399650.0   1.900350e+10 496333.693305  41.574028           0.785596         926
          $50+ 5.870215e+07       4499250.0   2.001743e+10 965923.753666  66.114809           0.750189         341


In [154]:
# 3. 按游戏类型分析最优定价策略
# 只分析前8个主要游戏类型
top_8_genres = [g for g, c in genre_counts.most_common(8)]

# 按游戏类型和价格区间分组
genre_price_revenue = games_with_genre[
    games_with_genre['Primary genre'].isin(top_8_genres)
].groupby(['Primary genre', 'Price category']).agg({
    'Estimated revenue': 'mean',
    'Estimated owners (mid)': 'mean',
    'Positive rate': 'mean',
    'AppID': 'count'
}).reset_index()

genre_price_revenue.columns = ['Genre', 'Price category', 'Avg revenue', 'Avg owners', 'Avg positive rate', 'Game count']

# 过滤掉样本量太小的组合（少于10个游戏）
genre_price_revenue = genre_price_revenue[genre_price_revenue['Game count'] >= 10]

# 为每个游戏类型找出平均收入最高的价格区间
best_price_by_genre = genre_price_revenue.loc[
    genre_price_revenue.groupby('Genre')['Avg revenue'].idxmax()
][['Genre', 'Price category', 'Avg revenue', 'Avg owners', 'Avg positive rate', 'Game count']]

print("各游戏类型的最优定价区间（基于平均收入）:")
print(best_price_by_genre.sort_values('Avg revenue', ascending=False).to_string(index=False))

各游戏类型的最优定价区间（基于平均收入）:
     Genre Price category  Avg revenue   Avg owners  Avg positive rate  Game count
    Action           $50+ 9.023761e+07 1.492965e+06           0.761294         172
  Strategy           $50+ 6.195110e+07 1.032857e+06           0.762519          14
       RPG           $50+ 4.471551e+07 7.123684e+05           0.805532          38
Simulation           $50+ 2.127605e+07 3.490909e+05           0.670287          44
 Adventure           $50+ 2.003416e+07 3.340625e+05           0.813100          16
    Casual         $30-50 1.473762e+07 4.156452e+05           0.798577          31
     Indie         $30-50 8.764627e+06 2.361458e+05           0.791474          48


In [155]:
# 4. 可视化：热力图展示不同类型游戏在各价格区间的收入表现

# 创建透视表
revenue_pivot = genre_price_revenue.pivot(
    index='Genre', 
    columns='Price category', 
    values='Avg revenue'
).fillna(0)

# 确保价格区间按顺序排列
revenue_pivot = revenue_pivot[[cat for cat in category_order if cat in revenue_pivot.columns]]

# 创建热力图
fig8 = px.imshow(revenue_pivot,
                 labels=dict(x="价格区间", y="游戏类型", color="平均收入 ($)"),
                 x=revenue_pivot.columns,
                 y=revenue_pivot.index,
                 title="不同游戏类型在各价格区间的平均收入热力图",
                 color_continuous_scale='YlOrRd',
                 aspect='auto')

fig8.update_xaxes(side="bottom")
fig8.update_layout(height=500)
fig8.show()

print("\n热力图说明：")
print("- 颜色越深（红色），表示该类型游戏在该价格区间的平均收入越高")
print("- 白色或浅色区域表示该类型游戏在该价格区间样本不足或收入较低")


热力图说明：
- 颜色越深（红色），表示该类型游戏在该价格区间的平均收入越高
- 白色或浅色区域表示该类型游戏在该价格区间样本不足或收入较低


In [156]:
# 5. 可视化：不同类型游戏的价格-收入关系散点图

# 为每个主要类型创建散点图
fig9 = px.scatter(games_with_genre[games_with_genre['Primary genre'].isin(top_8_genres)].sample(
                      min(8000, len(games_with_genre))
                  ),
                  x='Price',
                  y='Estimated revenue',
                  color='Primary genre',
                  size='Positive rate',
                  hover_data=['Name', 'Estimated owners (mid)', 'Total reviews'],
                  title='不同游戏类型的价格 vs 收入估算 (气泡大小=好评率)',
                  labels={
                      'Price': '价格 ($)',
                      'Estimated revenue': '收入估算 ($)',
                      'Primary genre': '游戏类型',
                      'Positive rate': '好评率'
                  },
                  log_y=True)

fig9.update_layout(height=600)
fig9.show()

# 创建箱线图：展示各类型在不同价格区间的收入分布
fig10 = px.box(games_with_genre[games_with_genre['Primary genre'].isin(top_8_genres)],
               x='Price category',
               y='Estimated revenue',
               color='Primary genre',
               title='各游戏类型在不同价格区间的收入分布',
               labels={
                   'Price category': '价格区间',
                   'Estimated revenue': '收入估算 ($)',
                   'Primary genre': '游戏类型'
               },
               category_orders={'Price category': category_order},
               log_y=True)

fig10.update_layout(height=600)
fig10.show()

---

## 任务2.2：游戏类型与定价的交互效应深度分析

在这个阶段，我们将：
1. 创建多维度的价格表现矩阵（收入、好评率、玩家数）
2. 识别每个类型的"甜蜜定价区间"（综合考虑多个指标）
3. 分析价格提升对不同类型游戏的影响差异

In [157]:
# 1. 为主要游戏类型创建多维度价格表现矩阵
# 分析维度：收入、好评率、平均拥有者数、游戏数量

# 选择前6个主要类型进行详细分析
top_6_genres = [g for g, c in genre_counts.most_common(6)]

# 创建详细的类型×价格表现矩阵
detailed_performance = games_with_genre[
    games_with_genre['Primary genre'].isin(top_6_genres)
].groupby(['Primary genre', 'Price category']).agg({
    'Estimated revenue': ['mean', 'median'],
    'Estimated owners (mid)': 'mean',
    'Positive rate': 'mean',
    'Peak CCU': 'mean',
    'Total reviews': 'mean',
    'AppID': 'count'
}).reset_index()

# 扁平化列名
detailed_performance.columns = ['Genre', 'Price category', 'Avg revenue', 'Median revenue', 
                                'Avg owners', 'Avg positive rate', 'Avg peak CCU', 
                                'Avg total reviews', 'Game count']

# 只保留样本量足够的组合（至少10个游戏）
detailed_performance = detailed_performance[detailed_performance['Game count'] >= 10]

print("=== 游戏类型与价格区间的多维度表现矩阵 ===\n")

for genre in top_6_genres:
    genre_data = detailed_performance[detailed_performance['Genre'] == genre].copy()
    if len(genre_data) > 0:
        print(f"\n【{genre}】")
        print(genre_data[['Price category', 'Avg revenue', 'Avg owners', 'Avg positive rate', 'Game count']].to_string(index=False))
        print("-" * 80)

=== 游戏类型与价格区间的多维度表现矩阵 ===


【Indie】
Price category  Avg revenue    Avg owners  Avg positive rate  Game count
          $0-5 2.573868e+05  81474.747475           0.811111         495
        $10-20 2.776781e+06 162404.761905           0.838253         840
        $20-30 7.052219e+06 258230.088496           0.806857         226
        $30-50 8.764627e+06 236145.833333           0.791474          48
         $5-10 1.699743e+06 179281.609195           0.838214         522
            免费 0.000000e+00 103913.043478           0.759305          92
--------------------------------------------------------------------------------

【Casual】
Price category  Avg revenue    Avg owners  Avg positive rate  Game count
          $0-5 3.888986e+05 118281.733746           0.840324        1292
        $10-20 1.342982e+06  83054.474708           0.843827         514
        $20-30 3.052523e+06 111010.638298           0.821920          94
        $30-50 1.473762e+07 415645.161290           0.798577          

In [158]:
# 2. 识别每个类型的"甜蜜定价区间"
# 综合考虑：收入、好评率、玩家数量
# 策略：为每个指标标准化后，计算综合得分

from sklearn.preprocessing import MinMaxScaler

# 为每个游戏类型计算综合得分
sweet_spot_results = []

for genre in top_6_genres:
    genre_data = detailed_performance[detailed_performance['Genre'] == genre].copy()
    
    if len(genre_data) > 0:
        # 标准化三个关键指标（0-1范围）
        scaler = MinMaxScaler()
        
        # 收入（权重40%）
        genre_data['Revenue score'] = scaler.fit_transform(genre_data[['Avg revenue']]) * 0.4
        
        # 好评率（权重35%）
        genre_data['Rating score'] = scaler.fit_transform(genre_data[['Avg positive rate']]) * 0.35
        
        # 拥有者数量（权重25%）
        genre_data['Owners score'] = scaler.fit_transform(genre_data[['Avg owners']]) * 0.25
        
        # 综合得分
        genre_data['Total score'] = (genre_data['Revenue score'] + 
                                     genre_data['Rating score'] + 
                                     genre_data['Owners score'])
        
        # 找出得分最高的价格区间
        best_row = genre_data.loc[genre_data['Total score'].idxmax()]
        
        sweet_spot_results.append({
            'Genre': genre,
            'Sweet spot price': best_row['Price category'],
            'Total score': best_row['Total score'],
            'Avg revenue': best_row['Avg revenue'],
            'Avg positive rate': best_row['Avg positive rate'],
            'Avg owners': best_row['Avg owners'],
            'Game count': best_row['Game count']
        })

sweet_spot_df = pd.DataFrame(sweet_spot_results)
sweet_spot_df = sweet_spot_df.sort_values('Total score', ascending=False)

print("\n=== 各游戏类型的'甜蜜定价区间'（综合得分排名） ===\n")
print("综合得分 = 收入(40%) + 好评率(35%) + 拥有者数(25%)\n")
print(sweet_spot_df.to_string(index=False))


=== 各游戏类型的'甜蜜定价区间'（综合得分排名） ===

综合得分 = 收入(40%) + 好评率(35%) + 拥有者数(25%)

     Genre Sweet spot price  Total score  Avg revenue  Avg positive rate   Avg owners  Game count
     Indie           $20-30     0.782662 7.052219e+06           0.806857 2.582301e+05         226
  Strategy             $50+     0.764556 6.195110e+07           0.762519 1.032857e+06          14
    Casual           $30-50     0.761139 1.473762e+07           0.798577 4.156452e+05          31
 Adventure             $50+     0.631456 2.003416e+07           0.813100 3.340625e+05          16
Simulation           $30-50     0.617419 1.318658e+07           0.749760 3.188172e+05          93
    Action             $50+     0.616162 9.023761e+07           0.761294 1.492965e+06         172


In [159]:
# 3. 创建多个热力图展示类型×价格的交互效应

# 创建包含3个子图的热力图：收入、好评率、拥有者数
from plotly.subplots import make_subplots

# 准备三个透视表
revenue_heatmap = detailed_performance.pivot(
    index='Genre', columns='Price category', values='Avg revenue'
).fillna(0)

rating_heatmap = detailed_performance.pivot(
    index='Genre', columns='Price category', values='Avg positive rate'
).fillna(0)

owners_heatmap = detailed_performance.pivot(
    index='Genre', columns='Price category', values='Avg owners'
).fillna(0)

# 确保价格区间按顺序排列
for heatmap in [revenue_heatmap, rating_heatmap, owners_heatmap]:
    cols = [cat for cat in category_order if cat in heatmap.columns]
    heatmap = heatmap[cols]

# 创建2x2子图布局
fig11 = make_subplots(
    rows=2, cols=2,
    subplot_titles=('平均收入热力图', '平均好评率热力图', '平均拥有者数热力图', '综合得分对比'),
    specs=[[{'type': 'heatmap'}, {'type': 'heatmap'}],
           [{'type': 'heatmap'}, {'type': 'bar'}]],
    vertical_spacing=0.12,
    horizontal_spacing=0.15
)

# 添加收入热力图
fig11.add_trace(
    go.Heatmap(
        z=revenue_heatmap.values,
        x=[cat for cat in category_order if cat in revenue_heatmap.columns],
        y=revenue_heatmap.index,
        colorscale='YlOrRd',
        name='Revenue',
        showscale=True,
        colorbar=dict(x=0.46, y=0.77, len=0.35)
    ),
    row=1, col=1
)

# 添加好评率热力图
fig11.add_trace(
    go.Heatmap(
        z=rating_heatmap.values,
        x=[cat for cat in category_order if cat in rating_heatmap.columns],
        y=rating_heatmap.index,
        colorscale='RdYlGn',
        name='Rating',
        showscale=True,
        colorbar=dict(x=1.0, y=0.77, len=0.35)
    ),
    row=1, col=2
)

# 添加拥有者数热力图
fig11.add_trace(
    go.Heatmap(
        z=owners_heatmap.values,
        x=[cat for cat in category_order if cat in owners_heatmap.columns],
        y=owners_heatmap.index,
        colorscale='Blues',
        name='Owners',
        showscale=True,
        colorbar=dict(x=0.46, y=0.23, len=0.35)
    ),
    row=2, col=1
)

# 添加综合得分柱状图
fig11.add_trace(
    go.Bar(
        x=sweet_spot_df['Genre'],
        y=sweet_spot_df['Total score'],
        text=sweet_spot_df['Sweet spot price'],
        textposition='outside',
        name='Total Score',
        marker_color='lightblue'
    ),
    row=2, col=2
)

fig11.update_layout(
    height=900,
    title_text="游戏类型与定价的多维度交互效应分析",
    showlegend=False
)

fig11.update_xaxes(tickangle=45)
fig11.show()

In [160]:
# 4. 分析价格与好评率的权衡关系
# 研究：价格提升时，好评率如何变化？不同类型是否有不同的敏感度？

price_rating_tradeoff = []

for genre in top_6_genres:
    genre_data = detailed_performance[detailed_performance['Genre'] == genre].copy()
    
    # 按价格区间排序并计算变化率
    if len(genre_data) >= 3:  # 至少有3个价格点
        # 提取价格区间的中位数作为数值
        price_midpoint = {
            '免费': 0, '$0-5': 2.5, '$5-10': 7.5, '$10-20': 15,
            '$20-30': 25, '$30-50': 40, '$50+': 60
        }
        
        genre_data['Price midpoint'] = genre_data['Price category'].map(price_midpoint)
        genre_data = genre_data.sort_values('Price midpoint')
        
        # 计算好评率变化趋势（最高价 vs 最低价）
        if len(genre_data) >= 2:
            low_price = genre_data.iloc[0]
            high_price = genre_data.iloc[-1]
            
            rating_change = high_price['Avg positive rate'] - low_price['Avg positive rate']
            revenue_change_pct = ((high_price['Avg revenue'] - low_price['Avg revenue']) / 
                                  (low_price['Avg revenue'] + 1)) * 100
            
            price_rating_tradeoff.append({
                'Genre': genre,
                'Low price range': low_price['Price category'],
                'High price range': high_price['Price category'],
                'Rating change': rating_change,
                'Revenue change %': revenue_change_pct,
                'Low price rating': low_price['Avg positive rate'],
                'High price rating': high_price['Avg positive rate']
            })

tradeoff_df = pd.DataFrame(price_rating_tradeoff)
tradeoff_df = tradeoff_df.sort_values('Rating change', ascending=False)

print("\n=== 价格提升对好评率的影响分析 ===\n")
print("分析：从最低价格区间提升到最高价格区间时的影响\n")
print(tradeoff_df.to_string(index=False))

print("\n【解读】")
print("- Rating change > 0: 价格提升后好评率反而提高（高端市场更满意）")
print("- Rating change < 0: 价格提升后好评率下降（价格敏感度高）")
print("- Rating change ≈ 0: 价格对好评率影响不大（质量决定口碑）")


=== 价格提升对好评率的影响分析 ===

分析：从最低价格区间提升到最高价格区间时的影响

     Genre Low price range High price range  Rating change  Revenue change %  Low price rating  High price rating
     Indie              免费           $30-50       0.032169      8.764627e+08          0.759305           0.791474
  Strategy              免费             $50+       0.030396      6.195110e+09          0.732124           0.762519
    Casual              免费           $30-50       0.021603      1.473762e+09          0.776975           0.798577
    Action              免费             $50+       0.007136      9.023761e+09          0.754158           0.761294
Simulation              免费             $50+       0.003377      2.127605e+09          0.666909           0.670287
 Adventure              免费             $50+      -0.005541      2.003416e+09          0.818640           0.813100

【解读】
- Rating change > 0: 价格提升后好评率反而提高（高端市场更满意）
- Rating change < 0: 价格提升后好评率下降（价格敏感度高）
- Rating change ≈ 0: 价格对好评率影响不大（质量决定口碑）


In [161]:
# 5. 可视化：不同类型游戏在各价格区间的表现曲线

# 为每个类型创建价格-表现曲线
fig12 = make_subplots(
    rows=2, cols=3,
    subplot_titles=top_6_genres,
    specs=[[{'secondary_y': True}, {'secondary_y': True}, {'secondary_y': True}],
           [{'secondary_y': True}, {'secondary_y': True}, {'secondary_y': True}]],
    vertical_spacing=0.12,
    horizontal_spacing=0.1
)

price_midpoint_map = {
    '免费': 0, '$0-5': 2.5, '$5-10': 7.5, '$10-20': 15,
    '$20-30': 25, '$30-50': 40, '$50+': 60
}

positions = [(1,1), (1,2), (1,3), (2,1), (2,2), (2,3)]

for idx, genre in enumerate(top_6_genres):
    genre_data = detailed_performance[detailed_performance['Genre'] == genre].copy()
    genre_data['Price midpoint'] = genre_data['Price category'].map(price_midpoint_map)
    genre_data = genre_data.sort_values('Price midpoint')
    
    row, col = positions[idx]
    
    # 添加收入曲线（主轴）
    fig12.add_trace(
        go.Scatter(
            x=genre_data['Price midpoint'],
            y=genre_data['Avg revenue'],
            name='Revenue',
            mode='lines+markers',
            line=dict(color='orange', width=2),
            showlegend=(idx==0)
        ),
        row=row, col=col,
        secondary_y=False
    )
    
    # 添加好评率曲线（次轴）
    fig12.add_trace(
        go.Scatter(
            x=genre_data['Price midpoint'],
            y=genre_data['Avg positive rate'],
            name='Positive Rate',
            mode='lines+markers',
            line=dict(color='green', width=2, dash='dash'),
            showlegend=(idx==0)
        ),
        row=row, col=col,
        secondary_y=True
    )

# 更新布局
fig12.update_layout(
    height=800,
    title_text="各游戏类型的价格-收入-好评率关系曲线",
    hovermode='x unified'
)

# 更新y轴标签
for i in range(1, 7):
    row = (i-1) // 3 + 1
    col = (i-1) % 3 + 1
    fig12.update_yaxes(title_text="收入 ($)", row=row, col=col, secondary_y=False)
    fig12.update_yaxes(title_text="好评率", row=row, col=col, secondary_y=True, range=[0.6, 1.0])
    fig12.update_xaxes(title_text="价格 ($)", row=row, col=col)

fig12.show()

In [162]:
# 6. 总结：为开发者提供定价建议决策表

print("\n" + "="*80)
print("【开发者定价决策指南】基于游戏类型与市场定位")
print("="*80 + "\n")

pricing_guide = []

for _, row in sweet_spot_df.iterrows():
    genre = row['Genre']
    sweet_price = row['Sweet spot price']
    avg_revenue = row['Avg revenue']
    avg_rating = row['Avg positive rate']
    
    # 根据甜蜜定价区间给出建议
    if sweet_price in ['$30-50', '$50+']:
        market = '高端市场'
        strategy = '高品质、高内容量、强IP或独特玩法'
    elif sweet_price in ['$10-20', '$20-30']:
        market = '中端市场'
        strategy = '平衡品质与价格，强调性价比'
    else:
        market = '大众市场'
        strategy = '低价策略，靠量取胜或免费+内购'
    
    pricing_guide.append({
        'Genre': genre,
        'Sweet Spot': sweet_price,
        'Market': market,
        'Expected Revenue': f'${avg_revenue:,.0f}',
        'Expected Rating': f'{avg_rating:.2%}',
        'Strategy': strategy
    })

guide_df = pd.DataFrame(pricing_guide)

for _, row in guide_df.iterrows():
    print(f"【{row['Genre']}】")
    print(f"  ✓ 推荐定价: {row['Sweet Spot']}")
    print(f"  ✓ 目标市场: {row['Market']}")
    print(f"  ✓ 预期收入: {row['Expected Revenue']}")
    print(f"  ✓ 预期好评率: {row['Expected Rating']}")
    print(f"  ✓ 成功策略: {row['Strategy']}")
    print()

print("="*80)
print("注意：以上建议基于历史数据统计，实际定价还需考虑游戏品质、竞品分析、营销预算等因素")
print("="*80)


【开发者定价决策指南】基于游戏类型与市场定位

【Indie】
  ✓ 推荐定价: $20-30
  ✓ 目标市场: 中端市场
  ✓ 预期收入: $7,052,219
  ✓ 预期好评率: 80.69%
  ✓ 成功策略: 平衡品质与价格，强调性价比

【Strategy】
  ✓ 推荐定价: $50+
  ✓ 目标市场: 高端市场
  ✓ 预期收入: $61,951,100
  ✓ 预期好评率: 76.25%
  ✓ 成功策略: 高品质、高内容量、强IP或独特玩法

【Casual】
  ✓ 推荐定价: $30-50
  ✓ 目标市场: 高端市场
  ✓ 预期收入: $14,737,618
  ✓ 预期好评率: 79.86%
  ✓ 成功策略: 高品质、高内容量、强IP或独特玩法

【Adventure】
  ✓ 推荐定价: $50+
  ✓ 目标市场: 高端市场
  ✓ 预期收入: $20,034,159
  ✓ 预期好评率: 81.31%
  ✓ 成功策略: 高品质、高内容量、强IP或独特玩法

【Simulation】
  ✓ 推荐定价: $30-50
  ✓ 目标市场: 高端市场
  ✓ 预期收入: $13,186,581
  ✓ 预期好评率: 74.98%
  ✓ 成功策略: 高品质、高内容量、强IP或独特玩法

【Action】
  ✓ 推荐定价: $50+
  ✓ 目标市场: 高端市场
  ✓ 预期收入: $90,237,614
  ✓ 预期好评率: 76.13%
  ✓ 成功策略: 高品质、高内容量、强IP或独特玩法

注意：以上建议基于历史数据统计，实际定价还需考虑游戏品质、竞品分析、营销预算等因素


---

## 任务2.3：游戏生命周期分析（使用时间序列数据）

在这个阶段，我们将：
1. 探索时间序列数据的特征
2. 分析代表性游戏的生命周期曲线
3. 识别不同类型游戏的生命周期模式
4. 研究价格变化对玩家数量的影响

In [163]:
# 1. 预处理时间序列数据

# 处理日期格式
# price_final: "YYYY/M/D"
# count_final, review_final: "YYYY-MM-DD"

price_data['date'] = pd.to_datetime(price_data['date'], format='%Y/%m/%d', errors='coerce')
player_count_data['date'] = pd.to_datetime(player_count_data['date'], format='%Y-%m-%d', errors='coerce')
review_count_data['date'] = pd.to_datetime(review_count_data['date'], format='%Y-%m-%d', errors='coerce')

print("=== 时间序列数据基本信息 ===\n")

print("【价格数据 (price_final.csv)】")
print(f"  日期范围: {price_data['date'].min()} 到 {price_data['date'].max()}")
print(f"  总记录数: {len(price_data):,}")
print(f"  游戏数量: {price_data['AppID'].nunique():,}")
print(f"  平均每游戏数据点: {len(price_data) / price_data['AppID'].nunique():.1f}")

print("\n【玩家数量数据 (count_final.csv)】")
print(f"  日期范围: {player_count_data['date'].min()} 到 {player_count_data['date'].max()}")
print(f"  总记录数: {len(player_count_data):,}")
print(f"  游戏数量: {player_count_data['AppID'].nunique():,}")
print(f"  平均每游戏数据点: {len(player_count_data) / player_count_data['AppID'].nunique():.1f}")

print("\n【评论数量数据 (review_final.csv)】")
print(f"  日期范围: {review_count_data['date'].min()} 到 {review_count_data['date'].max()}")
print(f"  总记录数: {len(review_count_data):,}")
print(f"  游戏数量: {review_count_data['AppID'].nunique():,}")
print(f"  平均每游戏数据点: {len(review_count_data) / review_count_data['AppID'].nunique():.1f}")

# 检查数据覆盖情况
common_appids = set(price_data['AppID'].unique()) & set(player_count_data['AppID'].unique()) & set(review_count_data['AppID'].unique())
print(f"\n三个数据集共同覆盖的游戏数: {len(common_appids):,}")

=== 时间序列数据基本信息 ===

【价格数据 (price_final.csv)】
  日期范围: 1997-11-14 00:00:00 到 2025-10-11 00:00:00
  总记录数: 419,614
  游戏数量: 18,498
  平均每游戏数据点: 22.7

【玩家数量数据 (count_final.csv)】
  日期范围: 2011-09-01 00:00:00 到 2025-10-01 00:00:00
  总记录数: 474,228
  游戏数量: 18,907
  平均每游戏数据点: 25.1

【评论数量数据 (review_final.csv)】
  日期范围: 2023-06-01 00:00:00 到 2025-10-01 00:00:00
  总记录数: 397,625
  游戏数量: 14,272
  平均每游戏数据点: 27.9

三个数据集共同覆盖的游戏数: 13,779


In [164]:
# 2. 选择代表性游戏进行生命周期分析
# 策略：选择收入高、数据完整、不同类型的游戏

# 从之前的分析中，我们知道收入最高的游戏
# 选择有完整时间序列数据的高收入游戏

# 获取有完整数据的游戏
games_with_timeseries = games_with_genre[games_with_genre['AppID'].isin(common_appids)].copy()

print(f"有完整时间序列数据的游戏数: {len(games_with_timeseries):,}")

# 选择不同类型的代表性游戏（收入前3的有完整数据的游戏）
representative_games = []

for genre in top_6_genres:
    genre_games = games_with_timeseries[games_with_timeseries['Primary genre'] == genre]
    if len(genre_games) > 0:
        # 选择该类型收入最高的游戏
        top_game = genre_games.nlargest(1, 'Estimated revenue').iloc[0]
        representative_games.append({
            'AppID': top_game['AppID'],
            'Name': top_game['Name'],
            'Genre': genre,
            'Revenue': top_game['Estimated revenue'],
            'Price': top_game['Price']
        })

representative_df = pd.DataFrame(representative_games)

print("\n=== 选定的代表性游戏 ===\n")
print(representative_df.to_string(index=False))

有完整时间序列数据的游戏数: 10,526

=== 选定的代表性游戏 ===

  AppID                         Name      Genre      Revenue  Price
   4000                  Garry's Mod      Indie  349650000.0   9.99
 427520                     Factorio     Casual  225000000.0  30.00
2358720           Black Myth: Wukong     Action 4499250000.0  59.99
 322330        Don't Starve Together  Adventure  224850000.0  14.99
 255710             Cities: Skylines Simulation  224925000.0  29.99
 289070 Sid Meier’s Civilization® VI   Strategy  449925000.0  59.99


In [165]:
# 3. 创建生命周期曲线可视化

# 为每个代表性游戏创建生命周期图（玩家数量、评论数、价格随时间变化）
fig13 = make_subplots(
    rows=3, cols=2,
    subplot_titles=[f"{row['Name'][:30]}..." if len(row['Name']) > 30 else row['Name'] 
                    for _, row in representative_df.head(6).iterrows()],
    specs=[[{'secondary_y': True}, {'secondary_y': True}],
           [{'secondary_y': True}, {'secondary_y': True}],
           [{'secondary_y': True}, {'secondary_y': True}]],
    vertical_spacing=0.12,
    horizontal_spacing=0.1
)

positions = [(1,1), (1,2), (2,1), (2,2), (3,1), (3,2)]

for idx, (_, game) in enumerate(representative_df.head(6).iterrows()):
    app_id = game['AppID']
    row, col = positions[idx]
    
    # 获取该游戏的时间序列数据
    game_players = player_count_data[player_count_data['AppID'] == app_id].sort_values('date')
    game_price = price_data[price_data['AppID'] == app_id].sort_values('date')
    game_reviews = review_count_data[review_count_data['AppID'] == app_id].sort_values('date')
    
    # 添加玩家数量曲线（主轴）
    if len(game_players) > 0:
        fig13.add_trace(
            go.Scatter(
                x=game_players['date'],
                y=game_players['avg_players'],
                name=f'Avg Players',
                mode='lines',
                line=dict(color='blue', width=1.5),
                showlegend=(idx==0)
            ),
            row=row, col=col,
            secondary_y=False
        )
    
    # 添加价格曲线（次轴）
    if len(game_price) > 0:
        fig13.add_trace(
            go.Scatter(
                x=game_price['date'],
                y=game_price['price'],
                name=f'Price',
                mode='lines',
                line=dict(color='red', width=1.5, dash='dash'),
                showlegend=(idx==0)
            ),
            row=row, col=col,
            secondary_y=True
        )

# 更新布局
fig13.update_layout(
    height=1000,
    title_text="代表性游戏的生命周期曲线（玩家数量 vs 价格）",
    hovermode='x unified'
)

# 更新y轴标签
for i in range(1, 7):
    row = (i-1) // 2 + 1
    col = (i-1) % 2 + 1
    fig13.update_yaxes(title_text="平均玩家数", row=row, col=col, secondary_y=False)
    fig13.update_yaxes(title_text="价格 ($)", row=row, col=col, secondary_y=True)

fig13.show()

In [166]:
# 4. 分析价格变化与玩家数量的关系

# 策略：检测价格下降事件（可能是促销），分析对玩家数的影响

price_impact_analysis = []

for _, game in representative_df.iterrows():
    app_id = game['AppID']
    
    # 合并价格和玩家数据
    game_price = price_data[price_data['AppID'] == app_id].sort_values('date')
    game_players = player_count_data[player_count_data['AppID'] == app_id].sort_values('date')
    
    if len(game_price) > 1 and len(game_players) > 1:
        # 合并数据（按月）
        merged = pd.merge(game_price, game_players, on='date', how='inner', suffixes=('', '_players'))
        
        if len(merged) > 0:
            # 计算价格变化百分比
            merged['price_change_pct'] = merged['price'].pct_change() * 100
            
            # 计算玩家数变化百分比
            merged['players_change_pct'] = merged['avg_players'].pct_change() * 100
            
            # 识别大幅降价事件（降价超过20%）
            price_drops = merged[merged['price_change_pct'] < -20]
            
            if len(price_drops) > 0:
                # 平均玩家数增长
                avg_player_increase = price_drops['players_change_pct'].mean()
                
                price_impact_analysis.append({
                    'Game': game['Name'],
                    'Genre': game['Genre'],
                    'Price drops count': len(price_drops),
                    'Avg price drop %': price_drops['price_change_pct'].mean(),
                    'Avg player increase %': avg_player_increase
                })

if len(price_impact_analysis) > 0:
    impact_df = pd.DataFrame(price_impact_analysis)
    
    print("\n=== 价格降低对玩家数量的影响分析 ===\n")
    print("（检测降价超过20%的事件）\n")
    print(impact_df.to_string(index=False))
    
    print("\n【解读】")
    print("- Price drops count: 检测到的大幅降价次数")
    print("- Avg price drop %: 平均降价幅度")
    print("- Avg player increase %: 降价后平均玩家数增长率")
else:
    print("\n未检测到显著的价格降低事件")


=== 价格降低对玩家数量的影响分析 ===

（检测降价超过20%的事件）

                        Game      Genre  Price drops count  Avg price drop %  Avg player increase %
                 Garry's Mod      Indie                  4        -43.293293               6.592849
          Black Myth: Wukong     Action                  1        -20.003334              26.847719
       Don't Starve Together  Adventure                  7        -66.044029               8.461970
            Cities: Skylines Simulation                  8        -73.156896               6.993170
Sid Meier’s Civilization® VI   Strategy                  4        -60.066355               7.326023

【解读】
- Price drops count: 检测到的大幅降价次数
- Avg price drop %: 平均降价幅度
- Avg player increase %: 降价后平均玩家数增长率


In [167]:
# 5. 识别生命周期模式

# 分析：游戏发布后的玩家数量变化趋势

lifecycle_patterns = []

for _, game in representative_df.iterrows():
    app_id = game['AppID']
    
    # 获取玩家数据
    game_players = player_count_data[player_count_data['AppID'] == app_id].sort_values('date')
    
    if len(game_players) >= 6:  # 至少6个月数据
        # 计算前6个月的平均玩家数（早期）
        early_avg = game_players.head(6)['avg_players'].mean()
        
        # 计算后6个月的平均玩家数（后期）
        late_avg = game_players.tail(6)['avg_players'].mean()
        
        # 计算峰值
        peak_players = game_players['avg_players'].max()
        peak_date = game_players[game_players['avg_players'] == peak_players]['date'].iloc[0]
        
        # 计算衰减率
        if early_avg > 0:
            decay_rate = ((early_avg - late_avg) / early_avg) * 100
        else:
            decay_rate = 0
        
        # 判断生命周期模式
        if decay_rate > 50:
            pattern = "快速衰减型"
        elif decay_rate > 20:
            pattern = "稳定衰减型"
        elif decay_rate > -20:
            pattern = "稳定维持型"
        else:
            pattern = "持续增长型"
        
        lifecycle_patterns.append({
            'Game': game['Name'],
            'Genre': game['Genre'],
            'Data months': len(game_players),
            'Early avg players': early_avg,
            'Late avg players': late_avg,
            'Peak players': peak_players,
            'Peak date': peak_date.strftime('%Y-%m'),
            'Decay rate %': decay_rate,
            'Pattern': pattern
        })

if len(lifecycle_patterns) > 0:
    patterns_df = pd.DataFrame(lifecycle_patterns)
    
    print("\n=== 游戏生命周期模式分析 ===\n")
    print(patterns_df.to_string(index=False))
    
    print("\n【模式定义】")
    print("- 快速衰减型: 玩家数下降 > 50%")
    print("- 稳定衰减型: 玩家数下降 20-50%")
    print("- 稳定维持型: 玩家数变化 ±20%以内")
    print("- 持续增长型: 玩家数增长 > 20%")
    
    # 统计各模式的分布
    pattern_dist = patterns_df['Pattern'].value_counts()
    print(f"\n【模式分布】")
    for pattern, count in pattern_dist.items():
        print(f"  {pattern}: {count} 款游戏")


=== 游戏生命周期模式分析 ===

                        Game      Genre  Data months  Early avg players  Late avg players  Peak players Peak date  Decay rate % Pattern
                 Garry's Mod      Indie           29       22091.666667      19480.666667         27291   2023-07     11.818936   稳定维持型
                    Factorio     Casual           29       11692.666667      15937.666667         52583   2024-11    -36.304806   持续增长型
          Black Myth: Wukong     Action           15      268636.500000      16646.166667       1049895   2024-08     93.803461   快速衰减型
       Don't Starve Together  Adventure           29       27988.500000      28101.166667         32210   2024-01     -0.402546   稳定维持型
            Cities: Skylines Simulation           29       16378.666667       8960.166667         19091   2023-07     45.293675   稳定衰减型
Sid Meier’s Civilization® VI   Strategy           29       41117.333333      30385.500000         52530   2024-06     26.100509   稳定衰减型

【模式定义】
- 快速衰减型: 玩家数下降 > 50

In [168]:
# 6. 总结：生命周期关键发现

print("\n" + "="*80)
print("【任务2.3 生命周期分析总结】")
print("="*80 + "\n")

print("1. 数据覆盖情况:")
print(f"   - 有完整时间序列数据的游戏: {len(games_with_timeseries):,} 款")
print(f"   - 三数据集共同覆盖: {len(common_appids):,} 款游戏")

if len(lifecycle_patterns) > 0:
    print(f"\n2. 生命周期模式:")
    for pattern, count in patterns_df['Pattern'].value_counts().items():
        pct = (count / len(patterns_df)) * 100
        print(f"   - {pattern}: {count} 款 ({pct:.1f}%)")
    
    print(f"\n3. 平均衰减率: {patterns_df['Decay rate %'].mean():.1f}%")
    print(f"   - 最高衰减: {patterns_df['Decay rate %'].max():.1f}%")
    print(f"   - 最低衰减: {patterns_df['Decay rate %'].min():.1f}%")

if len(price_impact_analysis) > 0:
    print(f"\n4. 价格促销效果:")
    print(f"   - 检测到 {impact_df['Price drops count'].sum():.0f} 次大幅降价事件")
    print(f"   - 平均降价幅度: {impact_df['Avg price drop %'].mean():.1f}%")
    print(f"   - 平均玩家数增长: {impact_df['Avg player increase %'].mean():.1f}%")

print("\n" + "="*80)
print("注意：以上分析基于代表性游戏样本，不代表所有游戏的表现")
print("="*80)


【任务2.3 生命周期分析总结】

1. 数据覆盖情况:
   - 有完整时间序列数据的游戏: 10,526 款
   - 三数据集共同覆盖: 13,779 款游戏

2. 生命周期模式:
   - 稳定维持型: 2 款 (33.3%)
   - 稳定衰减型: 2 款 (33.3%)
   - 持续增长型: 1 款 (16.7%)
   - 快速衰减型: 1 款 (16.7%)

3. 平均衰减率: 23.4%
   - 最高衰减: 93.8%
   - 最低衰减: -36.3%

4. 价格促销效果:
   - 检测到 24 次大幅降价事件
   - 平均降价幅度: -52.5%
   - 平均玩家数增长: 11.2%

注意：以上分析基于代表性游戏样本，不代表所有游戏的表现


---

# 阶段2补充：P0级关键任务

## 任务2.4：幸存者偏差修正 - 失败游戏分析与风险评估

**目标**: 分析被之前筛选排除的游戏（<10评价），修正幸存者偏差，提供真实的风险评估

**重要性**: ⭐⭐⭐⭐⭐ 
- 之前的分析排除了81%的游戏（90,234款）
- 当前结论可能高估了高价策略的成功率
- 必须提供"风险-收益"权衡建议

In [169]:
# 1. 分离成功游戏 vs 失败游戏

print("="*80)
print("【任务2.4：失败游戏分析与风险评估】")
print("="*80 + "\n")

# 定义成功游戏：至少10个评价
# 定义失败游戏：少于10个评价
success_threshold = 10

games_simlified['Success status'] = games_simlified['Total reviews'].apply(
    lambda x: 'Success' if x >= success_threshold else 'Failed'
)

# 基本统计
total_games = len(games_simlified)
success_games = len(games_simlified[games_simlified['Success status'] == 'Success'])
failed_games = len(games_simlified[games_simlified['Success status'] == 'Failed'])

print("【总体成功率】")
print(f"  总游戏数: {total_games:,}")
print(f"  成功游戏 (≥10评价): {success_games:,} ({success_games/total_games*100:.1f}%)")
print(f"  失败游戏 (<10评价): {failed_games:,} ({failed_games/total_games*100:.1f}%)")
print(f"\n  ⚠️ 之前的分析排除了 {failed_games:,} 款游戏，占总数的 {failed_games/total_games*100:.1f}%！")

【任务2.4：失败游戏分析与风险评估】

【总体成功率】
  总游戏数: 111,452
  成功游戏 (≥10评价): 47,040 (42.2%)
  失败游戏 (<10评价): 64,412 (57.8%)

  ⚠️ 之前的分析排除了 64,412 款游戏，占总数的 57.8%！


In [170]:
# 2. 按价格区间统计失败率

failure_rate_by_price = games_simlified.groupby('Price category').agg({
    'AppID': 'count',
    'Success status': lambda x: (x == 'Failed').sum()
}).reset_index()

failure_rate_by_price.columns = ['Price category', 'Total games', 'Failed games']
failure_rate_by_price['Success games'] = failure_rate_by_price['Total games'] - failure_rate_by_price['Failed games']
failure_rate_by_price['Failure rate %'] = (failure_rate_by_price['Failed games'] / failure_rate_by_price['Total games']) * 100
failure_rate_by_price['Success rate %'] = 100 - failure_rate_by_price['Failure rate %']

# 按价格顺序排列
failure_rate_by_price['Price category'] = pd.Categorical(
    failure_rate_by_price['Price category'],
    categories=category_order,
    ordered=True
)
failure_rate_by_price = failure_rate_by_price.sort_values('Price category')

print("\n【各价格区间的成功率/失败率】\n")
print(failure_rate_by_price[['Price category', 'Total games', 'Success games', 
                              'Failed games', 'Success rate %', 'Failure rate %']].to_string(index=False))

# 可视化：堆叠柱状图
fig14 = go.Figure()

fig14.add_trace(go.Bar(
    x=failure_rate_by_price['Price category'],
    y=failure_rate_by_price['Success games'],
    name='成功游戏',
    marker_color='lightgreen',
    text=failure_rate_by_price['Success games'],
    textposition='inside'
))

fig14.add_trace(go.Bar(
    x=failure_rate_by_price['Price category'],
    y=failure_rate_by_price['Failed games'],
    name='失败游戏',
    marker_color='lightcoral',
    text=failure_rate_by_price['Failed games'],
    textposition='inside'
))

fig14.update_layout(
    barmode='stack',
    title='各价格区间的成功/失败游戏分布',
    xaxis_title='价格区间',
    yaxis_title='游戏数量',
    height=400,
    legend=dict(x=0.7, y=0.95)
)

fig14.show()


【各价格区间的成功率/失败率】

Price category  Total games  Success games  Failed games  Success rate %  Failure rate %
            免费        23247           6244         17003       26.859380       73.140620
          $0-5        43912          16782         27130       38.217344       61.782656
         $5-10        22961          10443         12518       45.481469       54.518531
        $10-20        15906           9740          6166       61.234754       38.765246
        $20-30         3160           2297           863       72.689873       27.310127
        $30-50         1427           1082           345       75.823406       24.176594
          $50+          839            452           387       53.873659       46.126341


In [171]:
# 3. 按游戏类型统计失败率

# 为所有游戏添加主要类型
games_simlified['Primary genre'] = games_simlified['Genres'].apply(
    lambda x: str(x).split(',')[0].strip() if pd.notna(x) else 'Unknown'
)

# 只分析主要的游戏类型
failure_rate_by_genre = games_simlified[
    games_simlified['Primary genre'].isin(top_6_genres)
].groupby('Primary genre').agg({
    'AppID': 'count',
    'Success status': lambda x: (x == 'Failed').sum()
}).reset_index()

failure_rate_by_genre.columns = ['Genre', 'Total games', 'Failed games']
failure_rate_by_genre['Success games'] = failure_rate_by_genre['Total games'] - failure_rate_by_genre['Failed games']
failure_rate_by_genre['Failure rate %'] = (failure_rate_by_genre['Failed games'] / failure_rate_by_genre['Total games']) * 100
failure_rate_by_genre['Success rate %'] = 100 - failure_rate_by_genre['Failure rate %']
failure_rate_by_genre = failure_rate_by_genre.sort_values('Failure rate %', ascending=False)

print("\n【各游戏类型的成功率/失败率】\n")
print(failure_rate_by_genre.to_string(index=False))

# 可视化：失败率对比
fig15 = px.bar(failure_rate_by_genre,
               x='Genre',
               y='Failure rate %',
               title='各游戏类型的失败率对比',
               labels={'Genre': '游戏类型', 'Failure rate %': '失败率 (%)'},
               text='Failure rate %',
               color='Failure rate %',
               color_continuous_scale='Reds')

fig15.update_traces(texttemplate='%{text:.1f}%', textposition='outside')
fig15.update_layout(height=400, showlegend=False)
fig15.show()


【各游戏类型的成功率/失败率】

     Genre  Total games  Failed games  Success games  Failure rate %  Success rate %
    Casual        21428         13978           7450       65.232406       34.767594
    Action        42234         22604          19630       53.520860       46.479140
 Adventure        21619         11403          10216       52.745270       47.254730
     Indie         9851          5179           4672       52.573343       47.426657
Simulation         2283          1134           1149       49.671485       50.328515
  Strategy         1500           730            770       48.666667       51.333333


In [172]:
# 4. 交叉分析：游戏类型 × 价格区间的失败率矩阵

# 创建失败率热力图
failure_matrix = games_simlified[
    games_simlified['Primary genre'].isin(top_6_genres)
].groupby(['Primary genre', 'Price category']).agg({
    'AppID': 'count',
    'Success status': lambda x: (x == 'Failed').sum()
}).reset_index()

failure_matrix.columns = ['Genre', 'Price category', 'Total', 'Failed']
failure_matrix['Failure rate %'] = (failure_matrix['Failed'] / failure_matrix['Total']) * 100

# 只保留样本量足够的组合（至少20个游戏）
failure_matrix = failure_matrix[failure_matrix['Total'] >= 20]

# 创建透视表
failure_heatmap = failure_matrix.pivot(
    index='Genre',
    columns='Price category',
    values='Failure rate %'
).fillna(0)

# 确保价格区间按顺序排列
failure_heatmap = failure_heatmap[[cat for cat in category_order if cat in failure_heatmap.columns]]

print("\n【失败率矩阵：游戏类型 × 价格区间】\n")
print(failure_heatmap.round(1).to_string())

# 可视化热力图
fig16 = px.imshow(failure_heatmap,
                  labels=dict(x="价格区间", y="游戏类型", color="失败率 (%)"),
                  x=failure_heatmap.columns,
                  y=failure_heatmap.index,
                  title="失败率热力图：游戏类型 × 价格区间（颜色越深失败率越高）",
                  color_continuous_scale='Reds',
                  aspect='auto',
                  text_auto='.1f')

fig16.update_xaxes(side="bottom")
fig16.update_layout(height=500)
fig16.show()

print("\n【解读】")
print("- 数值表示该类型在该价格区间的失败率（%）")
print("- 只显示样本量≥20的组合，避免小样本偏差")
print("- 颜色越深（红色），失败风险越高")


【失败率矩阵：游戏类型 × 价格区间】

Price category    免费  $0-5  $5-10  $10-20  $20-30  $30-50  $50+
Genre                                                          
Action          62.1  60.8   53.5    35.7    22.4    15.7  43.8
Adventure       65.8  57.2   51.3    40.1    32.0    32.1  62.9
Casual          69.5  67.2   63.5    51.4    48.7    50.5  60.5
Indie           66.1  60.7   53.9    32.8    17.5    36.8  42.9
Simulation      62.0  61.6   53.4    43.8    23.0    18.3  43.5
Strategy        72.9  61.8   44.3    39.3    18.8     9.4  29.2



【解读】
- 数值表示该类型在该价格区间的失败率（%）
- 只显示样本量≥20的组合，避免小样本偏差
- 颜色越深（红色），失败风险越高


In [173]:
# 5. 失败游戏的特征分析

print("\n【失败游戏 vs 成功游戏的特征对比】\n")

# 对比成功和失败游戏的关键特征
success_data = games_simlified[games_simlified['Success status'] == 'Success']
failed_data = games_simlified[games_simlified['Success status'] == 'Failed']

feature_comparison = pd.DataFrame({
    'Feature': ['平均价格 ($)', '平均拥有者数', '平均Peak CCU', '平均好评率 (%)', 
                '有DLC的比例 (%)', '支持Windows (%)', '支持Mac (%)', '支持Linux (%)'],
    'Success games': [
        success_data['Price'].mean(),
        success_data['Estimated owners (mid)'].mean(),
        success_data['Peak CCU'].mean(),
        success_data['Positive rate'].mean() * 100,
        (success_data['DLC count'] > 0).sum() / len(success_data) * 100,
        success_data['Windows'].sum() / len(success_data) * 100,
        success_data['Mac'].sum() / len(success_data) * 100,
        success_data['Linux'].sum() / len(success_data) * 100
    ],
    'Failed games': [
        failed_data['Price'].mean(),
        failed_data['Estimated owners (mid)'].mean(),
        failed_data['Peak CCU'].mean(),
        failed_data['Positive rate'].mean() * 100,
        (failed_data['DLC count'] > 0).sum() / len(failed_data) * 100,
        failed_data['Windows'].sum() / len(failed_data) * 100,
        failed_data['Mac'].sum() / len(failed_data) * 100,
        failed_data['Linux'].sum() / len(failed_data) * 100
    ]
})

feature_comparison['Difference'] = feature_comparison['Success games'] - feature_comparison['Failed games']
print(feature_comparison.to_string(index=False))

print("\n【关键发现】")
print(f"- 失败游戏平均价格: ${failed_data['Price'].mean():.2f}")
print(f"- 成功游戏平均价格: ${success_data['Price'].mean():.2f}")
print(f"- 价格差异: ${feature_comparison.loc[0, 'Difference']:.2f}")
print(f"\n失败游戏的平均拥有者数仅为成功游戏的 {(failed_data['Estimated owners (mid)'].mean() / success_data['Estimated owners (mid)'].mean() * 100):.1f}%")


【失败游戏 vs 成功游戏的特征对比】

      Feature  Success games  Failed games    Difference
     平均价格 ($)       9.192210      5.505562      3.686648
       平均拥有者数  151368.516156   8227.193691 143141.322466
   平均Peak CCU     418.029252      2.225144    415.804107
    平均好评率 (%)      77.114954     31.161665     45.953289
  有DLC的比例 (%)      21.483844      5.710116     15.773727
支持Windows (%)      99.989371     99.956530      0.032841
    支持Mac (%)      24.880952     11.910824     12.970128
  支持Linux (%)      16.441327      9.240514      7.200812

【关键发现】
- 失败游戏平均价格: $5.51
- 成功游戏平均价格: $9.19
- 价格差异: $3.69

失败游戏的平均拥有者数仅为成功游戏的 5.4%


In [174]:
# 6. 高价失败游戏案例分析

# 识别高价但失败的游戏（$30+且<10评价）
high_price_failed = games_simlified[
    (games_simlified['Price'] >= 30) & 
    (games_simlified['Success status'] == 'Failed')
].copy()

print(f"\n【高价失败游戏分析】（定价≥$30但评价<10）\n")
print(f"高价失败游戏数量: {len(high_price_failed):,}")
print(f"占所有高价游戏的比例: {len(high_price_failed) / len(games_simlified[games_simlified['Price'] >= 30]) * 100:.1f}%")

# 按类型统计高价失败游戏
high_price_failed_by_genre = high_price_failed[
    high_price_failed['Primary genre'].isin(top_6_genres)
]['Primary genre'].value_counts()

print(f"\n高价失败游戏的类型分布:")
for genre, count in high_price_failed_by_genre.items():
    pct = count / len(high_price_failed) * 100
    print(f"  {genre}: {count} ({pct:.1f}%)")

# 展示一些高价失败游戏的样本（价格最高的10个）
high_price_failed_samples = high_price_failed.nlargest(10, 'Price')[
    ['Name', 'Price', 'Total reviews', 'Primary genre', 'Release year', 'DLC count']
]

print(f"\n高价失败游戏样本（价格最高的10个）:")
print(high_price_failed_samples.to_string(index=False))


【高价失败游戏分析】（定价≥$30但评价<10）

高价失败游戏数量: 732
占所有高价游戏的比例: 32.3%

高价失败游戏的类型分布:
  Action: 235 (32.1%)
  Adventure: 128 (17.5%)
  Casual: 102 (13.9%)
  Simulation: 60 (8.2%)
  Indie: 57 (7.8%)
  Strategy: 12 (1.6%)

高价失败游戏样本（价格最高的10个）:
                              Name  Price  Total reviews Primary genre  Release year  DLC count
                 The Leverage Game 999.98              0         Indie        2023.0          0
The Leverage Game Business Edition 999.98              0         Indie        2023.0          0
 Ascent Free-Roaming VR Experience 999.00              6        Action        2019.0          0
                         True Love 500.00              2        Action        2024.0          0
                         灰烬行星与填鸭少女 199.99              7        Casual        2020.0          0
                 Earthquake escape 199.99              2    Simulation        2021.0          0
                              安全教育 199.99              0     Adventure        2018.0          0
    

In [175]:
# 7. 创建风险评级系统

print("\n" + "="*80)
print("【定价策略风险评级表】")
print("="*80 + "\n")

# 为每个价格区间和类型组合创建风险评级
risk_rating = []

for _, row in failure_matrix.iterrows():
    genre = row['Genre']
    price_cat = row['Price category']
    failure_rate = row['Failure rate %']
    total_games = row['Total']
    
    # 风险等级判断
    if failure_rate >= 85:
        risk_level = "极高风险 🔴"
        recommendation = "强烈不推荐，成功率<15%"
    elif failure_rate >= 75:
        risk_level = "高风险 🟠"
        recommendation = "需要极强的质量和营销支持"
    elif failure_rate >= 65:
        risk_level = "中高风险 🟡"
        recommendation = "需要充分的质量保证和市场验证"
    elif failure_rate >= 50:
        risk_level = "中等风险 🟢"
        recommendation = "可尝试，但需要谨慎评估"
    else:
        risk_level = "较低风险 🟢"
        recommendation = "相对安全的定价策略"
    
    risk_rating.append({
        'Genre': genre,
        'Price range': price_cat,
        'Failure rate %': round(failure_rate, 1),
        'Success rate %': round(100 - failure_rate, 1),
        'Risk level': risk_level,
        'Sample size': total_games,
        'Recommendation': recommendation
    })

risk_df = pd.DataFrame(risk_rating)
risk_df = risk_df.sort_values('Failure rate %', ascending=False)

print(risk_df.to_string(index=False))

print("\n" + "="*80)
print("【使用说明】")
print("- 🔴 极高风险: 失败率≥85%，强烈不推荐")
print("- 🟠 高风险: 失败率75-85%，需要顶级质量支持")
print("- 🟡 中高风险: 失败率65-75%，需要充分准备")
print("- 🟢 中等/较低风险: 失败率<65%，相对安全")
print("="*80)


【定价策略风险评级表】

     Genre Price range  Failure rate %  Success rate % Risk level  Sample size Recommendation
  Strategy          免费            72.9            27.1     中高风险 🟡          177 需要充分的质量保证和市场验证
    Casual          免费            69.5            30.5     中高风险 🟡         3211 需要充分的质量保证和市场验证
    Casual        $0-5            67.2            32.8     中高风险 🟡        12081 需要充分的质量保证和市场验证
     Indie          免费            66.1            33.9     中高风险 🟡         1158 需要充分的质量保证和市场验证
 Adventure          免费            65.8            34.2     中高风险 🟡         3111 需要充分的质量保证和市场验证
    Casual       $5-10            63.5            36.5     中等风险 🟢         3932    可尝试，但需要谨慎评估
 Adventure        $50+            62.9            37.1     中等风险 🟢           62    可尝试，但需要谨慎评估
    Action          免费            62.1            37.9     中等风险 🟢         6694    可尝试，但需要谨慎评估
Simulation          免费            62.0            38.0     中等风险 🟢          316    可尝试，但需要谨慎评估
  Strategy        $0-5            61.8        

In [176]:
# 8. 任务2.4总结

print("\n" + "="*80)
print("【任务2.4 关键发现总结】")
print("="*80 + "\n")

print("1. 幸存者偏差的严重性:")
print(f"   - 之前的分析排除了 {failed_games:,} 款游戏（{failed_games/total_games*100:.1f}%）")
print(f"   - 仅分析了 {success_games:,} 款成功游戏（{success_games/total_games*100:.1f}%）")
print(f"   - ⚠️ 结论可能严重高估了成功概率")

print(f"\n2. 真实成功率:")
print(f"   - 总体成功率: {success_games/total_games*100:.1f}%")
print(f"   - 这意味着约 {failed_games/total_games*100:.0f}% 的游戏未能获得足够市场关注")

print(f"\n3. 价格区间失败率:")
highest_failure = failure_rate_by_price.loc[failure_rate_by_price['Failure rate %'].idxmax()]
lowest_failure = failure_rate_by_price.loc[failure_rate_by_price['Failure rate %'].idxmin()]
print(f"   - 失败率最高: {highest_failure['Price category']} ({highest_failure['Failure rate %']:.1f}%)")
print(f"   - 失败率最低: {lowest_failure['Price category']} ({lowest_failure['Failure rate %']:.1f}%)")

print(f"\n4. 游戏类型失败率:")
for idx, row in failure_rate_by_genre.head(3).iterrows():
    print(f"   - {row['Genre']}: {row['Failure rate %']:.1f}%")

print(f"\n5. 失败游戏的特征:")
print(f"   - 平均价格比成功游戏{'高' if failed_data['Price'].mean() > success_data['Price'].mean() else '低'} ${abs(failed_data['Price'].mean() - success_data['Price'].mean()):.2f}")
print(f"   - 平均拥有者数仅为成功游戏的 {failed_data['Estimated owners (mid)'].mean() / success_data['Estimated owners (mid)'].mean() * 100:.1f}%")

print(f"\n6. 高价失败游戏:")
print(f"   - $30+失败游戏数量: {len(high_price_failed):,}")
print(f"   - 占所有高价游戏: {len(high_price_failed) / len(games_simlified[games_simlified['Price'] >= 30]) * 100:.1f}%")

print("\n" + "="*80)
print("【重要警示】")
print("- 高价策略存在巨大风险，大部分高价游戏未能成功")
print("- 定价决策必须基于游戏质量、营销能力、市场验证")
print("- 不要仅根据'成功游戏的平均收入'做决策，要考虑成功概率")
print("="*80)


【任务2.4 关键发现总结】

1. 幸存者偏差的严重性:
   - 之前的分析排除了 64,412 款游戏（36391.0%）
   - 仅分析了 47,040 款成功游戏（26576.3%）
   - ⚠️ 结论可能严重高估了成功概率

2. 真实成功率:
   - 总体成功率: 26576.3%
   - 这意味着约 36391% 的游戏未能获得足够市场关注

3. 价格区间失败率:
   - 失败率最高: 免费 (73.1%)
   - 失败率最低: $30-50 (24.2%)

4. 游戏类型失败率:
   - Casual: 65.2%
   - Action: 53.5%
   - Adventure: 52.7%

5. 失败游戏的特征:
   - 平均价格比成功游戏低 $3.69
   - 平均拥有者数仅为成功游戏的 5.4%

6. 高价失败游戏:
   - $30+失败游戏数量: 732
   - 占所有高价游戏: 32.3%

【重要警示】
- 高价策略存在巨大风险，大部分高价游戏未能成功
- 定价决策必须基于游戏质量、营销能力、市场验证
- 不要仅根据'成功游戏的平均收入'做决策，要考虑成功概率


---

## 任务2.5：DLC商业模式分析

**目标**: 分析DLC count对游戏表现的影响，识别DLC驱动型商业模式

**重要性**: ⭐⭐⭐⭐⭐
- 之前的收入估算仅基于基础游戏价格
- 完全忽略了DLC收入（Strategy/Simulation类可能DLC收入超过基础游戏）
- 可能改变最优定价策略结论

In [177]:
# 1. DLC数据基本统计

print("="*80)
print("【任务2.5：DLC商业模式分析】")
print("="*80 + "\n")

print("【DLC数据基本统计】\n")

# DLC count分布
print(f"总游戏数: {len(games_simlified):,}")
print(f"有DLC的游戏数: {(games_simlified['DLC count'] > 0).sum():,} ({(games_simlified['DLC count'] > 0).sum() / len(games_simlified) * 100:.1f}%)")
print(f"无DLC的游戏数: {(games_simlified['DLC count'] == 0).sum():,} ({(games_simlified['DLC count'] == 0).sum() / len(games_simlified) * 100:.1f}%)")

print(f"\nDLC count统计:")
print(f"  平均DLC数: {games_simlified['DLC count'].mean():.2f}")
print(f"  中位数DLC数: {games_simlified['DLC count'].median():.0f}")
print(f"  最大DLC数: {games_simlified['DLC count'].max()}")

# 创建DLC分组
def dlc_category(count):
    if count == 0:
        return '无DLC'
    elif count <= 5:
        return '低DLC (1-5)'
    elif count <= 15:
        return '中DLC (6-15)'
    else:
        return '高DLC (16+)'

games_simlified['DLC category'] = games_simlified['DLC count'].apply(dlc_category)

dlc_dist = games_simlified['DLC category'].value_counts()
print(f"\nDLC分组分布:")
for cat in ['无DLC', '低DLC (1-5)', '中DLC (6-15)', '高DLC (16+)']:
    if cat in dlc_dist.index:
        count = dlc_dist[cat]
        pct = count / len(games_simlified) * 100
        print(f"  {cat}: {count:,} ({pct:.1f}%)")

【任务2.5：DLC商业模式分析】

【DLC数据基本统计】

总游戏数: 111,452
有DLC的游戏数: 13,784 (12.4%)
无DLC的游戏数: 97,668 (87.6%)

DLC count统计:
  平均DLC数: 0.45
  中位数DLC数: 0
  最大DLC数: 2366

DLC分组分布:
  无DLC: 97,668 (87.6%)
  低DLC (1-5): 12,712 (11.4%)
  中DLC (6-15): 735 (0.7%)
  高DLC (16+): 337 (0.3%)


In [178]:
# 2. DLC count与收入/好评率的关系（仅成功游戏）

print("\n【DLC与游戏表现的关系】（仅分析成功游戏≥10评价）\n")

# 使用之前筛选的成功游戏数据
success_games_df = games_simlified[games_simlified['Success status'] == 'Success'].copy()

dlc_performance = success_games_df.groupby('DLC category').agg({
    'Estimated owners (mid)': 'mean',
    'Price': 'mean',
    'Positive rate': 'mean',
    'Total reviews': 'mean',
    'Peak CCU': 'mean',
    'AppID': 'count'
}).reset_index()

dlc_performance.columns = ['DLC category', 'Avg owners', 'Avg price', 
                            'Avg positive rate', 'Avg reviews', 'Avg peak CCU', 'Game count']

# 计算估算收入（基础游戏收入）
dlc_performance['Avg base revenue'] = dlc_performance['Avg owners'] * dlc_performance['Avg price']

# 按DLC数量排序
dlc_order = ['无DLC', '低DLC (1-5)', '中DLC (6-15)', '高DLC (16+)']
dlc_performance['DLC category'] = pd.Categorical(dlc_performance['DLC category'], 
                                                  categories=dlc_order, ordered=True)
dlc_performance = dlc_performance.sort_values('DLC category')

print(dlc_performance.to_string(index=False))

# 可视化：DLC数量与表现的关系
fig17 = make_subplots(
    rows=2, cols=2,
    subplot_titles=('DLC数量 vs 平均拥有者数', 'DLC数量 vs 基础收入', 
                    'DLC数量 vs 好评率', 'DLC数量 vs 平均价格'),
    specs=[[{'type': 'bar'}, {'type': 'bar'}],
           [{'type': 'bar'}, {'type': 'bar'}]]
)

fig17.add_trace(go.Bar(x=dlc_performance['DLC category'], y=dlc_performance['Avg owners'], 
                       marker_color='lightblue', text=dlc_performance['Avg owners'],
                       texttemplate='%{text:.0f}', textposition='outside'), row=1, col=1)
fig17.add_trace(go.Bar(x=dlc_performance['DLC category'], y=dlc_performance['Avg base revenue'], 
                       marker_color='orange', text=dlc_performance['Avg base revenue'],
                       texttemplate='%{text:.2s}', textposition='outside'), row=1, col=2)
fig17.add_trace(go.Bar(x=dlc_performance['DLC category'], y=dlc_performance['Avg positive rate'], 
                       marker_color='green', text=dlc_performance['Avg positive rate'],
                       texttemplate='%{text:.2f}', textposition='outside'), row=2, col=1)
fig17.add_trace(go.Bar(x=dlc_performance['DLC category'], y=dlc_performance['Avg price'], 
                       marker_color='purple', text=dlc_performance['Avg price'],
                       texttemplate='$%{text:.2f}', textposition='outside'), row=2, col=2)

fig17.update_layout(height=800, title_text="DLC数量对游戏表现的影响", showlegend=False)
fig17.update_xaxes(tickangle=45)
fig17.show()


【DLC与游戏表现的关系】（仅分析成功游戏≥10评价）

DLC category   Avg owners  Avg price  Avg positive rate  Avg reviews  Avg peak CCU  Game count  Avg base revenue
        无DLC 9.100273e+04   8.016977           0.761336   893.985542    151.155927       36934      7.295668e+05
  低DLC (1-5) 2.854281e+05  12.495618           0.809522  4642.001086   1159.720122        9204      3.566600e+06
 中DLC (6-15) 1.008563e+06  21.885217           0.777242 20497.179775   1728.808989         623      2.207263e+07
  高DLC (16+) 1.805968e+06  27.449427           0.790784 33998.003584   8351.939068         279      4.957278e+07


In [179]:
# 3. 按游戏类型分析DLC策略

print("\n【各游戏类型的DLC策略对比】\n")

dlc_by_genre = success_games_df[
    success_games_df['Primary genre'].isin(top_6_genres)
].groupby('Primary genre').agg({
    'DLC count': ['mean', 'median', 'max'],
    'AppID': 'count'
}).reset_index()

dlc_by_genre.columns = ['Genre', 'Avg DLC', 'Median DLC', 'Max DLC', 'Game count']
dlc_by_genre = dlc_by_genre.sort_values('Avg DLC', ascending=False)

print(dlc_by_genre.to_string(index=False))

# 可视化：各类型的平均DLC数量
fig18 = px.bar(dlc_by_genre,
               x='Genre',
               y='Avg DLC',
               title='各游戏类型的平均DLC数量',
               labels={'Genre': '游戏类型', 'Avg DLC': '平均DLC数量'},
               text='Avg DLC',
               color='Avg DLC',
               color_continuous_scale='Blues')

fig18.update_traces(texttemplate='%{text:.1f}', textposition='outside')
fig18.update_layout(height=400, showlegend=False)
fig18.show()

print("\n【解读】")
print("- 平均DLC数量越高，说明该类型更依赖DLC商业模式")
print("- Strategy/Simulation类通常DLC密集，适合长期运营")


【各游戏类型的DLC策略对比】

     Genre  Avg DLC  Median DLC  Max DLC  Game count
Simulation 5.008703         0.0      678        1149
     Indie 1.402825         0.0     2366        4672
  Strategy 0.805195         0.0       22         770
    Action 0.689353         0.0      461       19630
    Casual 0.659060         0.0     1555        7450
 Adventure 0.421985         0.0       37       10216



【解读】
- 平均DLC数量越高，说明该类型更依赖DLC商业模式
- Strategy/Simulation类通常DLC密集，适合长期运营


In [180]:
# 4. DLC密集型游戏案例研究

print("\n【DLC密集型游戏案例分析】（DLC≥20）\n")

# 筛选DLC密集型成功游戏
dlc_heavy_games = success_games_df[success_games_df['DLC count'] >= 20].copy()
dlc_heavy_games['Estimated revenue'] = dlc_heavy_games['Estimated owners (mid)'] * dlc_heavy_games['Price']

print(f"DLC密集型游戏数量: {len(dlc_heavy_games):,}")
print(f"占成功游戏的比例: {len(dlc_heavy_games) / len(success_games_df) * 100:.1f}%")

# 展示收入最高的10个DLC密集型游戏
top_dlc_games = dlc_heavy_games.nlargest(10, 'Estimated revenue')[
    ['Name', 'Price', 'DLC count', 'Estimated owners (mid)', 'Estimated revenue', 
     'Primary genre', 'Positive rate']
]

print(f"\n收入最高的10个DLC密集型游戏:")
print(top_dlc_games.to_string(index=False))

# 对比：低价+高DLC vs 高价+低DLC
print(f"\n【商业模式对比】\n")

low_price_high_dlc = success_games_df[
    (success_games_df['Price'] < 30) & 
    (success_games_df['DLC count'] >= 10)
]

high_price_low_dlc = success_games_df[
    (success_games_df['Price'] >= 50) & 
    (success_games_df['DLC count'] < 5)
]

print(f"模式1：低价基础游戏+高DLC（<$30且DLC≥10）")
print(f"  游戏数量: {len(low_price_high_dlc):,}")
print(f"  平均基础价格: ${low_price_high_dlc['Price'].mean():.2f}")
print(f"  平均DLC数: {low_price_high_dlc['DLC count'].mean():.1f}")
print(f"  平均拥有者数: {low_price_high_dlc['Estimated owners (mid)'].mean():,.0f}")
print(f"  平均好评率: {low_price_high_dlc['Positive rate'].mean():.2%}")

print(f"\n模式2：高价基础游戏+低DLC（≥$50且DLC<5）")
print(f"  游戏数量: {len(high_price_low_dlc):,}")
print(f"  平均基础价格: ${high_price_low_dlc['Price'].mean():.2f}")
print(f"  平均DLC数: {high_price_low_dlc['DLC count'].mean():.1f}")
print(f"  平均拥有者数: {high_price_low_dlc['Estimated owners (mid)'].mean():,.0f}")
print(f"  平均好评率: {high_price_low_dlc['Positive rate'].mean():.2%}")


【DLC密集型游戏案例分析】（DLC≥20）

DLC密集型游戏数量: 221
占成功游戏的比例: 0.5%

收入最高的10个DLC密集型游戏:
                     Name  Price  DLC count  Estimated owners (mid)  Estimated revenue Primary genre  Positive rate
The Witcher® 3: Wild Hunt  39.99         22              15000000.0        599850000.0           RPG       0.961074
  Total War: WARHAMMER II  59.99         22               7500000.0        449925000.0        Action       0.929359
    Monster Hunter: World  29.99        200              15000000.0        449850000.0        Action       0.855376
                 PAYDAY 2   9.99         75              35000000.0        349650000.0        Action       0.892743
            Borderlands 2  19.99         48              15000000.0        299850000.0        Action       0.937249
   Euro Truck Simulator 2  19.99         79              15000000.0        299850000.0         Indie       0.973171
              Dying Light  29.99         34               7500000.0        224925000.0        Action       0.9502

In [181]:
# 5. DLC与价格策略的交互分析

print("\n【DLC数量 × 价格区间的交互效应】\n")

# 创建DLC和价格的组合分析（仅成功游戏）
dlc_price_matrix = success_games_df.groupby(['DLC category', 'Price category']).agg({
    'Estimated owners (mid)': 'mean',
    'Positive rate': 'mean',
    'AppID': 'count'
}).reset_index()

dlc_price_matrix.columns = ['DLC category', 'Price category', 'Avg owners', 'Avg positive rate', 'Game count']

# 只保留样本量足够的组合
dlc_price_matrix = dlc_price_matrix[dlc_price_matrix['Game count'] >= 10]

# 创建收入估算
dlc_price_matrix['Price midpoint'] = dlc_price_matrix['Price category'].map({
    '免费': 0, '$0-5': 2.5, '$5-10': 7.5, '$10-20': 15,
    '$20-30': 25, '$30-50': 40, '$50+': 60
})
dlc_price_matrix['Avg base revenue'] = dlc_price_matrix['Avg owners'] * dlc_price_matrix['Price midpoint']

# 创建热力图：DLC × 价格 → 基础收入
revenue_pivot = dlc_price_matrix.pivot(
    index='DLC category',
    columns='Price category',
    values='Avg base revenue'
).fillna(0)

revenue_pivot = revenue_pivot[[cat for cat in category_order if cat in revenue_pivot.columns]]

print("基础收入矩阵（DLC数量 × 价格区间）:")
print(revenue_pivot.applymap(lambda x: f'${x:,.0f}' if x > 0 else '-').to_string())

fig19 = px.imshow(revenue_pivot,
                  labels=dict(x="价格区间", y="DLC数量", color="平均基础收入 ($)"),
                  x=revenue_pivot.columns,
                  y=revenue_pivot.index,
                  title="DLC数量 × 价格区间 → 基础收入热力图",
                  color_continuous_scale='YlGn',
                  aspect='auto')

fig19.update_xaxes(side="bottom")
fig19.update_layout(height=500)
fig19.show()


【DLC数量 × 价格区间的交互效应】

基础收入矩阵（DLC数量 × 价格区间）:
Price category 免费      $0-5        $5-10       $10-20       $20-30       $30-50         $50+
DLC category                                                                                
中DLC (6-15)     -  $703,333   $4,342,724  $14,135,185  $28,412,946  $32,498,551  $43,161,905
低DLC (1-5)      -  $269,469   $1,376,568   $3,331,677   $8,179,139  $18,220,398  $73,945,588
无DLC            -  $118,704     $535,853   $1,366,164   $3,132,992  $12,644,203  $22,849,515
高DLC (16+)      -         -  $27,913,235  $35,020,588  $39,976,974  $33,081,356  $50,604,255


C:\Users\yewen\AppData\Local\Temp\ipykernel_25496\3915222536.py:34: FutureWarning:

DataFrame.applymap has been deprecated. Use DataFrame.map instead.



In [182]:
# 6. 任务2.5总结

print("\n" + "="*80)
print("【任务2.5 关键发现总结】")
print("="*80 + "\n")

print("1. DLC普及度:")
print(f"   - 有DLC的游戏: {(games_simlified['DLC count'] > 0).sum() / len(games_simlified) * 100:.1f}%")
print(f"   - 平均DLC数: {games_simlified['DLC count'].mean():.2f}个")

if len(dlc_performance) > 0:
    print(f"\n2. DLC与游戏表现:")
    high_dlc = dlc_performance[dlc_performance['DLC category'] == '高DLC (16+)'].iloc[0] if '高DLC (16+)' in dlc_performance['DLC category'].values else None
    no_dlc = dlc_performance[dlc_performance['DLC category'] == '无DLC'].iloc[0] if '无DLC' in dlc_performance['DLC category'].values else None
    
    if high_dlc is not None and no_dlc is not None:
        print(f"   - 高DLC游戏平均拥有者: {high_dlc['Avg owners']:,.0f}")
        print(f"   - 无DLC游戏平均拥有者: {no_dlc['Avg owners']:,.0f}")
        print(f"   - 差异: {(high_dlc['Avg owners'] / no_dlc['Avg owners'] - 1) * 100:+.1f}%")

if len(dlc_by_genre) > 0:
    print(f"\n3. 游戏类型DLC策略:")
    top_dlc_genre = dlc_by_genre.iloc[0]
    print(f"   - DLC最密集类型: {top_dlc_genre['Genre']} (平均{top_dlc_genre['Avg DLC']:.1f}个)")
    print(f"   - 最大DLC数: {dlc_by_genre['Max DLC'].max():.0f}个")

if len(dlc_heavy_games) > 0:
    print(f"\n4. DLC密集型游戏:")
    print(f"   - DLC≥20的游戏: {len(dlc_heavy_games):,}款")
    print(f"   - 占成功游戏比例: {len(dlc_heavy_games) / len(success_games_df) * 100:.1f}%")

if len(low_price_high_dlc) > 0 and len(high_price_low_dlc) > 0:
    print(f"\n5. 商业模式对比:")
    print(f"   - 低价+高DLC模式: {len(low_price_high_dlc):,}款，平均拥有者{low_price_high_dlc['Estimated owners (mid)'].mean():,.0f}")
    print(f"   - 高价+低DLC模式: {len(high_price_low_dlc):,}款，平均拥有者{high_price_low_dlc['Estimated owners (mid)'].mean():,.0f}")

print("\n" + "="*80)
print("【重要发现】")
print("- DLC密集型游戏往往有更大的玩家基数（Strategy/Simulation类）")
print("- '低价基础游戏+持续DLC'是重要的商业模式")
print("- 之前的收入估算忽略DLC，可能低估了长期运营游戏的真实收入")
print("="*80)


【任务2.5 关键发现总结】

1. DLC普及度:
   - 有DLC的游戏: 12.4%
   - 平均DLC数: 0.45个

2. DLC与游戏表现:
   - 高DLC游戏平均拥有者: 1,805,968
   - 无DLC游戏平均拥有者: 91,003
   - 差异: +1884.5%

3. 游戏类型DLC策略:
   - DLC最密集类型: Simulation (平均5.0个)
   - 最大DLC数: 2366个

4. DLC密集型游戏:
   - DLC≥20的游戏: 221款
   - 占成功游戏比例: 0.5%

5. 商业模式对比:
   - 低价+高DLC模式: 336款，平均拥有者1,897,470
   - 高价+低DLC模式: 332款，平均拥有者713,630

【重要发现】
- DLC密集型游戏往往有更大的玩家基数（Strategy/Simulation类）
- '低价基础游戏+持续DLC'是重要的商业模式
- 之前的收入估算忽略DLC，可能低估了长期运营游戏的真实收入


---

## 任务2.7：市场饱和度与发行时间分析

**目标**: 分析Steam市场的时间趋势，识别饱和类型和新兴机会

**重要性**: ⭐⭐⭐⭐
- 2024年发行了20,583款游戏（历史最高）
- 需要了解市场饱和度对成功率的影响
- 为即将发行的游戏提供时机选择建议

In [183]:
# 1. 发行量趋势分析（2010-2024）

print("="*80)
print("【任务2.7：市场饱和度与发行时间分析】")
print("="*80 + "\n")

# 筛选2010年后的数据（更有代表性）
games_recent = games_simlified[games_simlified['Release year'] >= 2010].copy()

print("【发行量趋势分析】（2010-2024）\n")

# 按年份统计总发行量
yearly_stats = games_recent.groupby('Release year').agg({
    'AppID': 'count',
    'Success status': lambda x: (x == 'Success').sum(),
    'Price': 'mean',
    'Estimated owners (mid)': 'mean',
    'Positive rate': 'mean'
}).reset_index()

yearly_stats.columns = ['Year', 'Total games', 'Success games', 'Avg price', 
                        'Avg owners', 'Avg positive rate']
yearly_stats['Success rate %'] = (yearly_stats['Success games'] / yearly_stats['Total games']) * 100
yearly_stats['Failed games'] = yearly_stats['Total games'] - yearly_stats['Success games']

print(yearly_stats.to_string(index=False))

# 可视化发行量趋势
fig20 = go.Figure()

fig20.add_trace(go.Bar(
    x=yearly_stats['Year'],
    y=yearly_stats['Success games'],
    name='成功游戏',
    marker_color='lightgreen'
))

fig20.add_trace(go.Bar(
    x=yearly_stats['Year'],
    y=yearly_stats['Failed games'],
    name='失败游戏',
    marker_color='lightcoral'
))

fig20.update_layout(
    barmode='stack',
    title='年度游戏发行量趋势（成功 vs 失败）',
    xaxis_title='年份',
    yaxis_title='游戏数量',
    height=400,
    hovermode='x unified'
)

fig20.show()

print(f"\n【关键发现】")
print(f"- 2010年发行量: {yearly_stats[yearly_stats['Year'] == 2010]['Total games'].values[0]:.0f}款")
print(f"- 2024年发行量: {yearly_stats[yearly_stats['Year'] == 2024]['Total games'].values[0]:.0f}款")
print(f"- 增长倍数: {yearly_stats[yearly_stats['Year'] == 2024]['Total games'].values[0] / yearly_stats[yearly_stats['Year'] == 2010]['Total games'].values[0]:.1f}倍")

【任务2.7：市场饱和度与发行时间分析】

【发行量趋势分析】（2010-2024）

  Year  Total games  Success games  Avg price   Avg owners  Avg positive rate  Success rate %  Failed games
2010.0          300            260   8.144433 4.532500e+05           0.750262       86.666667            40
2011.0          286            279   9.050874 7.880944e+05           0.746368       97.552448             7
2012.0          356            343   9.318848 9.318680e+05           0.736797       96.348315            13
2013.0          490            462  10.882327 1.164510e+06           0.711031       94.285714            28
2014.0         1627           1598   8.667179 2.813675e+05           0.683359       98.217578            29
2015.0         2683           2562   7.517816 2.274730e+05           0.686581       95.490123           121
2016.0         4407           3934   6.967765 1.516723e+05           0.701633       89.267075           473
2017.0         6324           4806   6.706659 1.158539e+05           0.687853       75.99620


【关键发现】
- 2010年发行量: 300款
- 2024年发行量: 20583款
- 增长倍数: 68.6倍


In [184]:
# 2. 成功率时间趋势分析

print("\n【成功率变化趋势】\n")

# 创建成功率趋势图
fig21 = make_subplots(
    rows=2, cols=2,
    subplot_titles=('成功率趋势', '平均拥有者数趋势', '平均价格趋势', '平均好评率趋势'),
    specs=[[{'secondary_y': False}, {'secondary_y': False}],
           [{'secondary_y': False}, {'secondary_y': False}]]
)

# 成功率趋势
fig21.add_trace(
    go.Scatter(x=yearly_stats['Year'], y=yearly_stats['Success rate %'],
               mode='lines+markers', name='成功率',
               line=dict(color='green', width=3),
               marker=dict(size=8)),
    row=1, col=1
)

# 平均拥有者数趋势
fig21.add_trace(
    go.Scatter(x=yearly_stats['Year'], y=yearly_stats['Avg owners'],
               mode='lines+markers', name='平均拥有者',
               line=dict(color='blue', width=3),
               marker=dict(size=8)),
    row=1, col=2
)

# 平均价格趋势
fig21.add_trace(
    go.Scatter(x=yearly_stats['Year'], y=yearly_stats['Avg price'],
               mode='lines+markers', name='平均价格',
               line=dict(color='orange', width=3),
               marker=dict(size=8)),
    row=2, col=1
)

# 平均好评率趋势
fig21.add_trace(
    go.Scatter(x=yearly_stats['Year'], y=yearly_stats['Avg positive rate'],
               mode='lines+markers', name='平均好评率',
               line=dict(color='purple', width=3),
               marker=dict(size=8)),
    row=2, col=2
)

fig21.update_xaxes(title_text="年份", row=1, col=1)
fig21.update_xaxes(title_text="年份", row=1, col=2)
fig21.update_xaxes(title_text="年份", row=2, col=1)
fig21.update_xaxes(title_text="年份", row=2, col=2)

fig21.update_yaxes(title_text="成功率 (%)", row=1, col=1)
fig21.update_yaxes(title_text="平均拥有者数", row=1, col=2)
fig21.update_yaxes(title_text="平均价格 ($)", row=2, col=1)
fig21.update_yaxes(title_text="平均好评率", row=2, col=2)

fig21.update_layout(height=800, title_text="市场表现指标时间趋势", showlegend=False)
fig21.show()

# 计算关键年份对比
print("【关键年份对比】\n")
years_compare = [2015, 2020, 2024]
for year in years_compare:
    if year in yearly_stats['Year'].values:
        row = yearly_stats[yearly_stats['Year'] == year].iloc[0]
        print(f"{year}年:")
        print(f"  发行量: {row['Total games']:.0f}款")
        print(f"  成功率: {row['Success rate %']:.1f}%")
        print(f"  平均拥有者: {row['Avg owners']:,.0f}")
        print(f"  平均好评率: {row['Avg positive rate']:.2%}")
        print()


【成功率变化趋势】



【关键年份对比】

2015年:
  发行量: 2683款
  成功率: 95.5%
  平均拥有者: 227,473
  平均好评率: 68.66%

2020年:
  发行量: 9631款
  成功率: 56.7%
  平均拥有者: 62,345
  平均好评率: 68.41%

2024年:
  发行量: 20583款
  成功率: 16.2%
  平均拥有者: 14,756
  平均好评率: 30.44%



In [185]:
# 3. 按游戏类型分析时间趋势

print("\n【各游戏类型的时间趋势】\n")

# 只分析主要类型在2015年后的趋势
games_recent_2015 = games_recent[
    (games_recent['Release year'] >= 2015) &
    (games_recent['Primary genre'].isin(top_6_genres))
].copy()

# 按年份和类型统计
genre_yearly = games_recent_2015.groupby(['Release year', 'Primary genre']).agg({
    'AppID': 'count',
    'Success status': lambda x: (x == 'Success').sum()
}).reset_index()

genre_yearly.columns = ['Year', 'Genre', 'Total games', 'Success games']
genre_yearly['Success rate %'] = (genre_yearly['Success games'] / genre_yearly['Total games']) * 100

# 为每个类型创建发行量趋势
fig22 = px.line(genre_yearly, 
                x='Year', 
                y='Total games', 
                color='Genre',
                title='各游戏类型年度发行量趋势（2015-2024）',
                labels={'Year': '年份', 'Total games': '发行量', 'Genre': '游戏类型'},
                markers=True,
                line_shape='spline')

fig22.update_layout(height=500, hovermode='x unified')
fig22.show()

# 计算各类型的增长率（2015 vs 2024）
print("【各类型发行量变化（2015 vs 2024）】\n")

for genre in top_6_genres:
    genre_data = genre_yearly[genre_yearly['Genre'] == genre]
    
    if 2015 in genre_data['Year'].values and 2024 in genre_data['Year'].values:
        count_2015 = genre_data[genre_data['Year'] == 2015]['Total games'].values[0]
        count_2024 = genre_data[genre_data['Year'] == 2024]['Total games'].values[0]
        growth = ((count_2024 - count_2015) / count_2015) * 100
        
        print(f"{genre}:")
        print(f"  2015年: {count_2015:.0f}款")
        print(f"  2024年: {count_2024:.0f}款")
        print(f"  增长率: {growth:+.1f}%")
        print()


【各游戏类型的时间趋势】



【各类型发行量变化（2015 vs 2024）】

Indie:
  2015年: 323款
  2024年: 1781款
  增长率: +451.4%

Casual:
  2015年: 302款
  2024年: 4335款
  增长率: +1335.4%

Action:
  2015年: 1167款
  2024年: 6995款
  增长率: +499.4%

Adventure:
  2015年: 585款
  2024年: 3950款
  增长率: +575.2%

Simulation:
  2015年: 68款
  2024年: 408款
  增长率: +500.0%

Strategy:
  2015年: 43款
  2024年: 274款
  增长率: +537.2%



In [186]:
# 4. 各类型成功率的时间趋势

print("\n【各类型成功率变化趋势】\n")

# 创建成功率趋势图
fig23 = px.line(genre_yearly,
                x='Year',
                y='Success rate %',
                color='Genre',
                title='各游戏类型成功率趋势（2015-2024）',
                labels={'Year': '年份', 'Success rate %': '成功率 (%)', 'Genre': '游戏类型'},
                markers=True,
                line_shape='spline')

fig23.update_layout(height=500, hovermode='x unified')
fig23.show()

# 计算各类型的成功率变化（2015 vs 2024）
print("【各类型成功率变化（2015 vs 2024）】\n")

success_rate_changes = []

for genre in top_6_genres:
    genre_data = genre_yearly[genre_yearly['Genre'] == genre]
    
    if 2015 in genre_data['Year'].values and 2024 in genre_data['Year'].values:
        rate_2015 = genre_data[genre_data['Year'] == 2015]['Success rate %'].values[0]
        rate_2024 = genre_data[genre_data['Year'] == 2024]['Success rate %'].values[0]
        change = rate_2024 - rate_2015
        
        success_rate_changes.append({
            'Genre': genre,
            'Success rate 2015': rate_2015,
            'Success rate 2024': rate_2024,
            'Change': change
        })
        
        print(f"{genre}:")
        print(f"  2015年成功率: {rate_2015:.1f}%")
        print(f"  2024年成功率: {rate_2024:.1f}%")
        print(f"  变化: {change:+.1f}百分点")
        print()

# 识别饱和类型（成功率下降最严重）
if len(success_rate_changes) > 0:
    success_rate_df = pd.DataFrame(success_rate_changes)
    success_rate_df = success_rate_df.sort_values('Change')
    
    print("\n【市场饱和度评估】\n")
    print("成功率下降最严重的类型（可能饱和）:")
    for _, row in success_rate_df.head(3).iterrows():
        print(f"  - {row['Genre']}: 下降{-row['Change']:.1f}百分点")
    
    print("\n成功率上升的类型（仍有机会）:")
    rising = success_rate_df[success_rate_df['Change'] > 0]
    if len(rising) > 0:
        for _, row in rising.iterrows():
            print(f"  - {row['Genre']}: 上升{row['Change']:.1f}百分点")
    else:
        print("  无（所有类型成功率都在下降）")


【各类型成功率变化趋势】



【各类型成功率变化（2015 vs 2024）】

Indie:
  2015年成功率: 94.4%
  2024年成功率: 19.0%
  变化: -75.4百分点

Casual:
  2015年成功率: 94.0%
  2024年成功率: 12.3%
  变化: -81.7百分点

Action:
  2015年成功率: 96.4%
  2024年成功率: 19.9%
  变化: -76.5百分点

Adventure:
  2015年成功率: 97.3%
  2024年成功率: 20.8%
  变化: -76.5百分点

Simulation:
  2015年成功率: 97.1%
  2024年成功率: 22.8%
  变化: -74.3百分点

Strategy:
  2015年成功率: 100.0%
  2024年成功率: 23.7%
  变化: -76.3百分点


【市场饱和度评估】

成功率下降最严重的类型（可能饱和）:
  - Casual: 下降81.7百分点
  - Action: 下降76.5百分点
  - Adventure: 下降76.5百分点

成功率上升的类型（仍有机会）:
  无（所有类型成功率都在下降）


In [187]:
# 5. 任务2.7总结：市场饱和度综合评估

print("\n" + "="*80)
print("【任务2.7 关键发现总结】")
print("="*80 + "\n")

print("1. 市场规模爆炸式增长:")
if len(yearly_stats) > 0:
    year_2010 = yearly_stats[yearly_stats['Year'] == 2010]['Total games'].values[0] if 2010 in yearly_stats['Year'].values else None
    year_2024 = yearly_stats[yearly_stats['Year'] == 2024]['Total games'].values[0] if 2024 in yearly_stats['Year'].values else None
    
    if year_2010 is not None and year_2024 is not None:
        print(f"   - 2010年发行量: {year_2010:.0f}款")
        print(f"   - 2024年发行量: {year_2024:.0f}款")
        print(f"   - 增长倍数: {year_2024/year_2010:.1f}倍")

print("\n2. 成功率整体趋势:")
if len(yearly_stats) > 0:
    overall_success_change = yearly_stats[yearly_stats['Year'] == 2024]['Success rate %'].values[0] - \
                            yearly_stats[yearly_stats['Year'] == 2015]['Success rate %'].values[0] \
                            if 2015 in yearly_stats['Year'].values and 2024 in yearly_stats['Year'].values else None
    
    if overall_success_change is not None:
        print(f"   - 2015-2024年成功率变化: {overall_success_change:+.1f}百分点")
        print(f"   - 趋势: {'市场竞争加剧' if overall_success_change < 0 else '市场环境改善'}")

print("\n3. 各类型市场状态:")
if len(success_rate_changes) > 0:
    for item in success_rate_changes:
        genre = item['Genre']
        change = item['Change']
        
        if change < -5:
            status = "🔴 严重饱和"
        elif change < 0:
            status = "🟠 轻微饱和"
        elif change > 5:
            status = "🟢 增长机会"
        else:
            status = "🟡 保持稳定"
        
        print(f"   - {genre}: {status} ({change:+.1f}百分点)")

# 2025-2026市场预测
print("\n4. 2025-2026年市场预测:")
print("   基于2015-2024年趋势:")
if len(yearly_stats) >= 5:
    # 简单线性预测
    recent_growth = (yearly_stats.iloc[-1]['Total games'] - yearly_stats.iloc[-5]['Total games']) / 5
    predicted_2025 = yearly_stats.iloc[-1]['Total games'] + recent_growth
    
    print(f"   - 预计2025年发行量: {predicted_2025:,.0f}款")
    print(f"   - 建议: 市场持续饱和，新游戏需要更强的差异化")

print("\n5. 开发者建议:")
print("   根据市场饱和度分析:")

# 识别相对安全的类型
if len(success_rate_changes) > 0:
    safe_genres = [item['Genre'] for item in success_rate_changes if item['Change'] >= -2]
    saturated_genres = [item['Genre'] for item in success_rate_changes if item['Change'] < -5]
    
    if len(safe_genres) > 0:
        print(f"   ✅ 相对安全的类型: {', '.join(safe_genres)}")
    
    if len(saturated_genres) > 0:
        print(f"   ⚠️ 避开饱和类型: {', '.join(saturated_genres)}")
    
    print(f"   💡 策略建议:")
    print(f"      - 专注差异化和创新，避免同质化竞争")
    print(f"      - 在成功率下降的类型中，质量更加重要")
    print(f"      - 考虑小众细分市场，避开红海")

print("\n" + "="*80)
print("注意：以上预测基于历史数据趋势，实际市场可能受突发事件影响")
print("="*80)


【任务2.7 关键发现总结】

1. 市场规模爆炸式增长:
   - 2010年发行量: 300款
   - 2024年发行量: 20583款
   - 增长倍数: 68.6倍

2. 成功率整体趋势:
   - 2015-2024年成功率变化: -79.2百分点
   - 趋势: 市场竞争加剧

3. 各类型市场状态:
   - Indie: 🔴 严重饱和 (-75.4百分点)
   - Casual: 🔴 严重饱和 (-81.7百分点)
   - Action: 🔴 严重饱和 (-76.5百分点)
   - Adventure: 🔴 严重饱和 (-76.5百分点)
   - Simulation: 🔴 严重饱和 (-74.3百分点)
   - Strategy: 🔴 严重饱和 (-76.3百分点)

4. 2025-2026年市场预测:
   基于2015-2024年趋势:
   - 预计2025年发行量: 4,769款
   - 建议: 市场持续饱和，新游戏需要更强的差异化

5. 开发者建议:
   根据市场饱和度分析:
   ⚠️ 避开饱和类型: Indie, Casual, Action, Adventure, Simulation, Strategy
   💡 策略建议:
      - 专注差异化和创新，避免同质化竞争
      - 在成功率下降的类型中，质量更加重要
      - 考虑小众细分市场，避开红海

注意：以上预测基于历史数据趋势，实际市场可能受突发事件影响


---

## 任务2.8：Tags标签分析与游戏特征深挖

**目标**: 分析Tags标签对游戏成功的影响，识别"黄金标签组合"

**重要性**: ⭐⭐⭐⭐
- Tags是玩家对游戏特征的直接标注
- 标签组合可能揭示成功游戏的隐藏模式
- 帮助开发者选择正确的游戏特征和营销标签

In [188]:
# 1. Tags数据清理和预处理

print("="*80)
print("【任务2.8：Tags标签分析】")
print("="*80 + "\n")

print("【Tags数据基本情况】\n")

# 检查Tags缺失情况
total_games = len(games_simlified)
games_with_tags = games_simlified['Tags'].notna().sum()
games_without_tags = games_simlified['Tags'].isna().sum()

print(f"总游戏数: {total_games:,}")
print(f"有Tags的游戏: {games_with_tags:,} ({games_with_tags/total_games*100:.1f}%)")
print(f"无Tags的游戏: {games_without_tags:,} ({games_without_tags/total_games*100:.1f}%)")

# 提取所有Tags（处理逗号分隔的字符串）
from collections import Counter

all_tags = []
for tags_str in games_simlified['Tags'].dropna():
    tags_list = [tag.strip() for tag in str(tags_str).split(',')]
    all_tags.extend(tags_list)

# 统计Tag频率
tag_counts = Counter(all_tags)
total_unique_tags = len(tag_counts)

print(f"\n总共有 {total_unique_tags:,} 种不同的Tags")
print(f"Tags总出现次数: {len(all_tags):,}")
print(f"平均每游戏Tags数: {len(all_tags)/games_with_tags:.1f}个")

# 展示最常见的20个Tags
print(f"\n【最常见的20个Tags】\n")
top_20_tags = tag_counts.most_common(20)
for i, (tag, count) in enumerate(top_20_tags, 1):
    pct = count / games_with_tags * 100
    print(f"{i:2d}. {tag:25s}: {count:6,} ({pct:5.1f}%)")

print("\n" + "="*80)

【任务2.8：Tags标签分析】

【Tags数据基本情况】

总游戏数: 111,452
有Tags的游戏: 74,029 (66.4%)
无Tags的游戏: 37,423 (33.6%)

总共有 453 种不同的Tags
Tags总出现次数: 982,724
平均每游戏Tags数: 13.3个

【最常见的20个Tags】

 1. Indie                    : 44,892 ( 60.6%)
 2. Singleplayer             : 40,923 ( 55.3%)
 3. Action                   : 32,864 ( 44.4%)
 4. Casual                   : 31,747 ( 42.9%)
 5. Adventure                : 31,082 ( 42.0%)
 6. 2D                       : 21,473 ( 29.0%)
 7. Simulation               : 15,825 ( 21.4%)
 8. Strategy                 : 15,780 ( 21.3%)
 9. RPG                      : 13,962 ( 18.9%)
10. Atmospheric              : 13,683 ( 18.5%)
11. 3D                       : 13,604 ( 18.4%)
12. Puzzle                   : 13,467 ( 18.2%)
13. Pixel Graphics           : 11,276 ( 15.2%)
14. Early Access             : 11,137 ( 15.0%)
15. Colorful                 : 11,106 ( 15.0%)
16. Story Rich               : 11,039 ( 14.9%)
17. Exploration              : 10,433 ( 14.1%)
18. Cute                     : 10,

In [189]:
# 2. Top 50 Tags的市场表现分析

print("\n【Top 50 Tags的市场表现对比】\n")

# 获取Top 50 Tags
top_50_tags = [tag for tag, count in tag_counts.most_common(50)]

# 为每个Tag分析其对应游戏的表现
tag_performance = []

for tag in top_50_tags:
    # 找出包含该Tag的所有游戏
    games_with_tag = games_simlified[
        games_simlified['Tags'].notna() & 
        games_simlified['Tags'].str.contains(tag, case=False, regex=False)
    ]
    
    if len(games_with_tag) > 0:
        # 区分成功和失败游戏
        success_games = games_with_tag[games_with_tag['Success status'] == 'Success']
        
        tag_performance.append({
            'Tag': tag,
            'Total games': len(games_with_tag),
            'Success games': len(success_games),
            'Success rate %': (len(success_games) / len(games_with_tag) * 100) if len(games_with_tag) > 0 else 0,
            'Avg price': success_games['Price'].mean() if len(success_games) > 0 else 0,
            'Avg owners': success_games['Estimated owners (mid)'].mean() if len(success_games) > 0 else 0,
            'Avg positive rate': success_games['Positive rate'].mean() if len(success_games) > 0 else 0,
            'Avg revenue': (success_games['Estimated owners (mid)'] * success_games['Price']).mean() if len(success_games) > 0 else 0
        })

tag_performance_df = pd.DataFrame(tag_performance)

# 按成功率排序
tag_performance_df_sorted = tag_performance_df.sort_values('Success rate %', ascending=False)

print("按成功率排序的Top 20 Tags:\n")
print(tag_performance_df_sorted.head(20)[['Tag', 'Total games', 'Success rate %', 'Avg owners', 'Avg positive rate']].to_string(index=False))

print("\n" + "-"*80)

# 按平均收入排序
tag_performance_df_revenue = tag_performance_df.sort_values('Avg revenue', ascending=False)

print("\n按平均收入排序的Top 20 Tags:\n")
print(tag_performance_df_revenue.head(20)[['Tag', 'Success games', 'Avg revenue', 'Avg price', 'Avg owners']].to_string(index=False))

# 可视化：成功率 vs 游戏数量
fig24 = px.scatter(tag_performance_df,
                   x='Total games',
                   y='Success rate %',
                   size='Avg owners',
                   color='Avg positive rate',
                   hover_data=['Tag', 'Success games'],
                   title='Top 50 Tags: 成功率 vs 游戏数量 (气泡大小=平均拥有者数)',
                   labels={
                       'Total games': '使用该Tag的游戏总数',
                       'Success rate %': '成功率 (%)',
                       'Avg owners': '平均拥有者数',
                       'Avg positive rate': '平均好评率'
                   },
                   color_continuous_scale='RdYlGn',
                   range_color=[0.5, 1.0],
                   log_x=True)

fig24.update_layout(height=600)
fig24.show()

print("\n【解读】")
print("- 气泡大小：平均拥有者数（越大说明该Tag的游戏市场表现越好）")
print("- 颜色：平均好评率（绿色=高好评，红色=低好评）")
print("- 横轴：使用该Tag的游戏总数（对数坐标）")
print("- 纵轴：成功率（获得至少10个评价的游戏比例）")


【Top 50 Tags的市场表现对比】

按成功率排序的Top 20 Tags:

                 Tag  Total games  Success rate %    Avg owners  Avg positive rate
               Anime         7087       77.719769  99385.439361           0.823175
           Difficult         5769       77.119085 310057.316251           0.814349
         Multiplayer        10844       76.410918 539013.999517           0.754455
  Female Protagonist         6240       74.535256 122081.272845           0.823264
          Open World         5481       73.399015 561885.408899           0.742640
        Visual Novel         4826       73.373394  53885.907936           0.850893
          Story Rich        11039       72.343509 212501.252191           0.831172
          Simulation        15825       69.990521 177544.691224           0.738385
Psychological Horror         4844       69.673823 138244.444444           0.797523
         Atmospheric        13683       69.641161 270453.352923           0.807239
                 RPG        15468       68.


【解读】
- 气泡大小：平均拥有者数（越大说明该Tag的游戏市场表现越好）
- 颜色：平均好评率（绿色=高好评，红色=低好评）
- 横轴：使用该Tag的游戏总数（对数坐标）
- 纵轴：成功率（获得至少10个评价的游戏比例）


In [190]:
# 3. 标签共现分析 - 找出最常见的Tag组合

print("\n" + "="*80)
print("【标签共现分析】")
print("="*80 + "\n")

# 分析成功游戏中常见的Tag组合
from itertools import combinations

# 只分析成功游戏的Tags
success_games_with_tags = games_simlified[
    (games_simlified['Success status'] == 'Success') & 
    (games_simlified['Tags'].notna())
].copy()

print(f"分析样本：{len(success_games_with_tags):,}款成功游戏\n")

# 统计2-Tag组合
tag_pairs = []
for tags_str in success_games_with_tags['Tags']:
    tags_list = [tag.strip() for tag in str(tags_str).split(',')]
    # 只保留Top 50的tags
    tags_list = [tag for tag in tags_list if tag in top_50_tags]
    
    # 生成所有2-tag组合
    if len(tags_list) >= 2:
        for pair in combinations(sorted(tags_list), 2):
            tag_pairs.append(pair)

# 统计组合频率
pair_counts = Counter(tag_pairs)

print("【最常见的20个Tag组合】\n")
print(f"{'排名':<4} {'Tag组合':<50} {'出现次数':>10} {'占成功游戏比例':>12}")
print("-" * 80)

for i, (pair, count) in enumerate(pair_counts.most_common(20), 1):
    tag1, tag2 = pair
    pct = count / len(success_games_with_tags) * 100
    print(f"{i:2d}.  {tag1} + {tag2:<35} {count:>10,} {pct:>11.1f}%")

# 分析每个组合的表现
print("\n" + "="*80)
print("【黄金Tag组合分析】（成功率 > 60% 且至少50款游戏）")
print("="*80 + "\n")

golden_combos = []

for (tag1, tag2), count in pair_counts.most_common(100):
    # 找出同时包含这两个Tag的所有游戏
    games_with_combo = games_simlified[
        games_simlified['Tags'].notna() & 
        games_simlified['Tags'].str.contains(tag1, case=False, regex=False) &
        games_simlified['Tags'].str.contains(tag2, case=False, regex=False)
    ]
    
    if len(games_with_combo) >= 50:  # 至少50款游戏
        success_games_combo = games_with_combo[games_with_combo['Success status'] == 'Success']
        success_rate = len(success_games_combo) / len(games_with_combo) * 100
        
        if success_rate > 60:  # 成功率超过60%
            golden_combos.append({
                'Tag combo': f"{tag1} + {tag2}",
                'Total games': len(games_with_combo),
                'Success rate %': success_rate,
                'Avg price': success_games_combo['Price'].mean() if len(success_games_combo) > 0 else 0,
                'Avg owners': success_games_combo['Estimated owners (mid)'].mean() if len(success_games_combo) > 0 else 0,
                'Avg positive rate': success_games_combo['Positive rate'].mean() if len(success_games_combo) > 0 else 0
            })

golden_combos_df = pd.DataFrame(golden_combos)
golden_combos_df = golden_combos_df.sort_values('Success rate %', ascending=False)

if len(golden_combos_df) > 0:
    print(golden_combos_df.head(15).to_string(index=False))
else:
    print("未找到符合条件的黄金组合（可能阈值太严格）")

print("\n【解读】")
print("- 黄金组合：成功率>60%且至少50款游戏的Tag组合")
print("- 这些组合可能揭示成功游戏的共同特征")
print("- 开发者可以考虑在游戏中融入这些特征组合")


【标签共现分析】

分析样本：47,039款成功游戏

【最常见的20个Tag组合】

排名   Tag组合                                                    出现次数      占成功游戏比例
--------------------------------------------------------------------------------
 1.  Indie + Singleplayer                            15,840        33.7%
 2.  Adventure + Indie                                   13,545        28.8%
 3.  Action + Indie                                   13,411        28.5%
 4.  Casual + Indie                                   13,237        28.1%
 5.  Adventure + Singleplayer                            12,319        26.2%
 6.  Action + Singleplayer                            11,268        24.0%
 7.  Casual + Singleplayer                            10,335        22.0%
 8.  Action + Adventure                                9,968        21.2%
 9.  2D + Singleplayer                             9,386        20.0%
10.  2D + Indie                                    8,291        17.6%
11.  Adventure + Casual                                  

In [191]:
# 4. 标签趋势分析 (2020 vs 2024) - 识别新兴和衰退的游戏特征

print("\n" + "="*80)
print("【标签趋势分析：2020 vs 2024】")
print("="*80 + "\n")

# 筛选2020和2024年发行的游戏
games_2020 = games_simlified[
    (games_simlified['Release year'] == 2020) &
    (games_simlified['Tags'].notna())
]

games_2024 = games_simlified[
    (games_simlified['Release year'] == 2024) &
    (games_simlified['Tags'].notna())
]

print(f"2020年发行游戏数（有Tags）: {len(games_2020):,}")
print(f"2024年发行游戏数（有Tags）: {len(games_2024):,}")

# 提取2020和2024的Tags
tags_2020 = []
for tags_str in games_2020['Tags']:
    tags_list = [tag.strip() for tag in str(tags_str).split(',')]
    tags_2020.extend(tags_list)

tags_2024 = []
for tags_str in games_2024['Tags']:
    tags_list = [tag.strip() for tag in str(tags_str).split(',')]
    tags_2024.extend(tags_list)

# 统计频率
tag_counts_2020 = Counter(tags_2020)
tag_counts_2024 = Counter(tags_2024)

# 只分析Top 50的Tags在两年的变化
tag_trends = []

for tag in top_50_tags:
    count_2020 = tag_counts_2020.get(tag, 0)
    count_2024 = tag_counts_2024.get(tag, 0)
    
    # 计算使用率（占当年游戏的比例）
    rate_2020 = (count_2020 / len(games_2020) * 100) if len(games_2020) > 0 else 0
    rate_2024 = (count_2024 / len(games_2024) * 100) if len(games_2024) > 0 else 0
    
    # 计算变化
    change = rate_2024 - rate_2020
    change_pct = ((rate_2024 - rate_2020) / rate_2020 * 100) if rate_2020 > 0 else 0
    
    tag_trends.append({
        'Tag': tag,
        'Rate 2020 %': rate_2020,
        'Rate 2024 %': rate_2024,
        'Change %': change,
        'Change pct': change_pct
    })

tag_trends_df = pd.DataFrame(tag_trends)

# 找出增长最快的Tags（新兴特征）
emerging_tags = tag_trends_df.sort_values('Change %', ascending=False).head(15)

print("\n【新兴Tag趋势】（2020→2024增长最快）\n")
print(emerging_tags[['Tag', 'Rate 2020 %', 'Rate 2024 %', 'Change %']].to_string(index=False))

# 找出衰退最快的Tags（过时特征）
declining_tags = tag_trends_df.sort_values('Change %', ascending=True).head(15)

print("\n" + "-"*80)
print("\n【衰退Tag趋势】（2020→2024下降最快）\n")
print(declining_tags[['Tag', 'Rate 2020 %', 'Rate 2024 %', 'Change %']].to_string(index=False))

# 可视化：Tag趋势对比
fig25 = go.Figure()

# 添加所有Tags的变化线
for _, row in tag_trends_df.iterrows():
    fig25.add_trace(go.Scatter(
        x=[2020, 2024],
        y=[row['Rate 2020 %'], row['Rate 2024 %']],
        mode='lines+markers',
        name=row['Tag'],
        line=dict(width=1),
        marker=dict(size=6),
        showlegend=False,
        hovertemplate=f"{row['Tag']}<br>2020: {row['Rate 2020 %']:.1f}%<br>2024: {row['Rate 2024 %']:.1f}%<extra></extra>"
    ))

# 高亮新兴和衰退的Tags
for _, row in emerging_tags.head(5).iterrows():
    fig25.add_trace(go.Scatter(
        x=[2020, 2024],
        y=[row['Rate 2020 %'], row['Rate 2024 %']],
        mode='lines+markers',
        name=f"↗ {row['Tag']}",
        line=dict(width=3, color='green'),
        marker=dict(size=10),
        showlegend=True
    ))

for _, row in declining_tags.head(5).iterrows():
    fig25.add_trace(go.Scatter(
        x=[2020, 2024],
        y=[row['Rate 2020 %'], row['Rate 2024 %']],
        mode='lines+markers',
        name=f"↘ {row['Tag']}",
        line=dict(width=3, color='red'),
        marker=dict(size=10),
        showlegend=True
    ))

fig25.update_layout(
    title='Tag使用率趋势：2020 vs 2024（Top 50 Tags）',
    xaxis_title='年份',
    yaxis_title='Tag使用率 (%)',
    height=600,
    hovermode='closest'
)

fig25.show()

print("\n【解读】")
print("- 绿色线：新兴Tag（增长最快的5个），代表市场新趋势")
print("- 红色线：衰退Tag（下降最快的5个），代表过时或饱和的特征")
print("- 灰色线：其他Top 50 Tags的变化轨迹")


【标签趋势分析：2020 vs 2024】

2020年发行游戏数（有Tags）: 8,669
2024年发行游戏数（有Tags）: 7,472

【新兴Tag趋势】（2020→2024增长最快）

                 Tag  Rate 2020 %  Rate 2024 %  Change %
                  3D    17.268428    36.603319 19.334891
        Singleplayer    59.568578    77.328694 17.760116
         Exploration    11.985235    25.575482 13.590247
          Controller     3.760526    14.306745 10.546219
        First-Person    13.519437    23.112955  9.593518
    Action-Adventure     9.089860    18.161135  9.071274
              Combat     5.975314    14.735011  8.759696
                  2D    30.326451    38.985546  8.659095
              Horror     9.781982    18.375268  8.593286
Psychological Horror     5.029415    13.209315  8.179900
           Realistic     5.894567    13.075482  7.180915
         Atmospheric    17.729842    24.531585  6.801743
                Cute    14.096205    20.610278  6.514074
                Dark     5.536971    11.870985  6.334014
          Story Rich    14.442266    20.5701


【解读】
- 绿色线：新兴Tag（增长最快的5个），代表市场新趋势
- 红色线：衰退Tag（下降最快的5个），代表过时或饱和的特征
- 灰色线：其他Top 50 Tags的变化轨迹


In [192]:
# 5. 任务2.8总结：Tags分析关键发现

print("\n" + "="*80)
print("【任务2.8 关键发现总结】")
print("="*80 + "\n")

print("1. Tags数据覆盖:")
print(f"   - 有Tags的游戏: {games_with_tags:,} ({games_with_tags/total_games*100:.1f}%)")
print(f"   - 总计不同Tags: {total_unique_tags:,} 种")
print(f"   - 平均每游戏Tags数: {len(all_tags)/games_with_tags:.1f}个")

if len(tag_performance_df) > 0:
    print(f"\n2. Top Tags市场表现:")
    top_success_tag = tag_performance_df_sorted.iloc[0]
    top_revenue_tag = tag_performance_df_revenue.iloc[0]
    print(f"   - 成功率最高Tag: {top_success_tag['Tag']} ({top_success_tag['Success rate %']:.1f}%)")
    print(f"   - 平均收入最高Tag: {top_revenue_tag['Tag']} (${top_revenue_tag['Avg revenue']:,.0f})")

if len(pair_counts) > 0:
    print(f"\n3. Tag组合分析:")
    most_common_pair = pair_counts.most_common(1)[0]
    print(f"   - 最常见组合: {most_common_pair[0][0]} + {most_common_pair[0][1]} ({most_common_pair[1]:,}次)")
    if len(golden_combos_df) > 0:
        print(f"   - 黄金组合数量: {len(golden_combos_df)}个（成功率>60%且≥50款游戏）")
        top_golden = golden_combos_df.iloc[0]
        print(f"   - 最佳黄金组合: {top_golden['Tag combo']} (成功率{top_golden['Success rate %']:.1f}%)")
    else:
        print(f"   - 黄金组合数量: 0个（阈值可能太严格）")

if len(tag_trends_df) > 0:
    print(f"\n4. Tag趋势洞察 (2020 vs 2024):")
    if len(emerging_tags) > 0:
        top_emerging = emerging_tags.iloc[0]
        print(f"   - 新兴Tag #1: {top_emerging['Tag']} (增长{top_emerging['Change %']:+.1f}个百分点)")
    if len(declining_tags) > 0:
        top_declining = declining_tags.iloc[0]
        print(f"   - 衰退Tag #1: {top_declining['Tag']} (下降{top_declining['Change %']:+.1f}个百分点)")

print("\n" + "="*80)
print("【开发者建议】")
print("="*80 + "\n")

print("基于Tags分析的游戏开发建议:")

if len(tag_performance_df_sorted) > 0:
    print("\n✅ 推荐融入的高成功率Tags:")
    for i, row in tag_performance_df_sorted.head(5).iterrows():
        if row['Success rate %'] > 50:
            print(f"   - {row['Tag']}: 成功率{row['Success rate %']:.1f}%，平均拥有者{row['Avg owners']:,.0f}")

if len(golden_combos_df) > 0:
    print("\n🎯 推荐的黄金Tag组合:")
    for i, row in golden_combos_df.head(3).iterrows():
        print(f"   - {row['Tag combo']}: 成功率{row['Success rate %']:.1f}%")

if len(emerging_tags) > 0:
    print("\n📈 抓住新兴趋势:")
    for i, row in emerging_tags.head(3).iterrows():
        if row['Change %'] > 0:
            print(f"   - {row['Tag']}: 2020→2024增长{row['Change %']:+.1f}%")

if len(declining_tags) > 0:
    print("\n⚠️ 避开衰退特征:")
    for i, row in declining_tags.head(3).iterrows():
        if row['Change %'] < -5:
            print(f"   - {row['Tag']}: 2020→2024下降{abs(row['Change %']):.1f}%，可能过度饱和")

print("\n" + "="*80)
print("注意：Tag选择应与游戏核心玩法一致，避免误导性标签")
print("="*80)


【任务2.8 关键发现总结】

1. Tags数据覆盖:
   - 有Tags的游戏: 74,029 (66.4%)
   - 总计不同Tags: 453 种
   - 平均每游戏Tags数: 13.3个

2. Top Tags市场表现:
   - 成功率最高Tag: Anime (77.7%)
   - 平均收入最高Tag: Open World ($10,444,919)

3. Tag组合分析:
   - 最常见组合: Indie + Singleplayer (15,840次)
   - 黄金组合数量: 76个（成功率>60%且≥50款游戏）
   - 最佳黄金组合: Atmospheric + Story Rich (成功率78.0%)

4. Tag趋势洞察 (2020 vs 2024):
   - 新兴Tag #1: 3D (增长+19.3个百分点)
   - 衰退Tag #1: Indie (下降-20.9个百分点)

【开发者建议】

基于Tags分析的游戏开发建议:

✅ 推荐融入的高成功率Tags:
   - Anime: 成功率77.7%，平均拥有者99,385
   - Difficult: 成功率77.1%，平均拥有者310,057
   - Multiplayer: 成功率76.4%，平均拥有者539,014
   - Female Protagonist: 成功率74.5%，平均拥有者122,081
   - Open World: 成功率73.4%，平均拥有者561,885

🎯 推荐的黄金Tag组合:
   - Atmospheric + Story Rich: 成功率78.0%
   - Action + Multiplayer: 成功率77.2%
   - Difficult + Indie: 成功率76.9%

📈 抓住新兴趋势:
   - 3D: 2020→2024增长+19.3%
   - Singleplayer: 2020→2024增长+17.8%
   - Exploration: 2020→2024增长+13.6%

⚠️ 避开衰退特征:
   - Indie: 2020→2024下降20.9%，可能过度饱和
   - VR: 2020→2024下降5.6%，可能过度饱和

注意：Tag选择应与游戏核心玩法一

---

# 🎮 阶段3：消费者视角 - 游戏购买决策支持

## 承接阶段2

**阶段2结论**：我们发现了成功游戏的特征（$30-50定价、DLC驱动、黄金标签）

**阶段3问题**：作为玩家，如何利用这些数据找到值得购买的游戏？

---

## 任务3.1：游戏性价比分析

**目标**: 帮助玩家找到"物有所值"的游戏

**分析维度**:
1. 价格 vs 游戏时长：每小时成本
2. 价格 vs 内容量：DLC、成就数量  
3. 价格 vs 评分：高评分低价游戏
4. 总拥有成本：基础价格 + DLC估算

**产出**:
- 性价比得分计算公式
- 各类型性价比之王推荐列表
- 每小时成本分布图
- 性价比排行榜

In [193]:
# 1. 创建改进的性价比得分计算公式

print("="*80)
print("【任务3.1：游戏性价比分析 - 改进版】")
print("="*80 + "\n")

# 改进1：提高质量门槛，过滤低质量游戏
# 只分析：付费游戏 + 有时长数据 + 有足够评论数 + 好评率达标
value_games = success_games_df[
    (success_games_df['Price'] > 0) &  # 付费游戏
    (success_games_df['Average playtime forever'] > 0) &  # 有游戏时长数据
    (success_games_df['Total reviews'] >= 50) &  # 提高到50个评论（更可靠）
    (success_games_df['Positive rate'] >= 0.6)  # 好评率至少60%
].copy()

print(f"分析样本：{len(value_games):,}款高质量付费游戏（好评率≥60%，评论≥50）\n")

# 计算关键指标

# 1. 每小时成本（价格 / 游戏时长（小时））
value_games['Playtime hours'] = value_games['Average playtime forever'] / 60
value_games['Cost per hour'] = value_games['Price'] / (value_games['Playtime hours'] + 1)  # +1避免除零

# 2. 改进的内容量指标
value_games['Content score'] = (
    value_games['DLC count'] * 5 +  # 降低DLC权重（每个DLC计5分）
    value_games['Achievements'] / 20 +  # 调整成就权重
    np.log1p(value_games['Playtime hours']) * 2  # 增加时长权重
)

# 3. 估算总拥有成本
value_games['Estimated DLC price'] = value_games['Price'] * 0.15 * value_games['DLC count']
value_games['Total ownership cost'] = value_games['Price'] + value_games['Estimated DLC price']

# 4. 改进的综合性价比得分
# 改进2：增加好评率权重（平方），提高质量的重要性
value_games['Value score raw'] = (
    (value_games['Positive rate'] ** 1.5) *  # 好评率1.5次方，奖励高质量
    np.log1p(value_games['Playtime hours']) *
    np.log1p(value_games['Content score'] + 1)
) / np.log1p(value_games['Total ownership cost'])

# 改进3：使用百分位数归一化（更均衡的分数分布）
from sklearn.preprocessing import MinMaxScaler

# 使用百分位数转换，分数分布更均衡
value_games['Value percentile'] = value_games['Value score raw'].rank(pct=True) * 100

# 同时提供线性归一化版本用于对比
scaler = MinMaxScaler(feature_range=(0, 100))
value_games['Value score linear'] = scaler.fit_transform(value_games[['Value score raw']])

# 使用百分位数作为主要得分
value_games['Value score'] = value_games['Value percentile']

print("【改进的性价比得分公式】")
print("Value Score = (好评率^1.5 × ln(游戏时长) × ln(内容分数)) / ln(总价格)")
print("\n改进点：")
print("  1. 质量门槛：要求好评率≥60%，评论数≥50（过滤低质量游戏）")
print("  2. 好评率权重：使用1.5次方，更重视游戏质量")
print("  3. 内容分数：降低DLC权重，增加游戏时长权重")
print("  4. 归一化方法：使用百分位数，分数分布更均衡")
print("  5. 最终分数：0-100分（百分位数排名）")

print(f"\n【性价比分数统计】")
print(f"平均性价比分数: {value_games['Value score'].mean():.1f}分")
print(f"中位数性价比分数: {value_games['Value score'].median():.1f}分")
print(f"最高性价比分数: {value_games['Value score'].max():.1f}分")
print(f"25分位数: {value_games['Value score'].quantile(0.25):.1f}分")
print(f"75分位数: {value_games['Value score'].quantile(0.75):.1f}分")

print(f"\n【每小时成本统计】")
print(f"平均每小时成本: ${value_games['Cost per hour'].mean():.2f}")
print(f"中位数每小时成本: ${value_games['Cost per hour'].median():.2f}")
print(f"最低每小时成本: ${value_games['Cost per hour'].min():.2f}")
print(f"最高每小时成本: ${value_games['Cost per hour'].max():.2f}")

print(f"\n【总拥有成本统计】")
print(f"平均总拥有成本: ${value_games['Total ownership cost'].mean():.2f}")
print(f"中位数总拥有成本: ${value_games['Total ownership cost'].median():.2f}")

print(f"\n【样本质量提升】")
print(f"  - 平均好评率: {value_games['Positive rate'].mean():.1%}")
print(f"  - 平均评论数: {value_games['Total reviews'].mean():,.0f}条")
print(f"  - 平均游戏时长: {value_games['Playtime hours'].mean():.1f}小时")

【任务3.1：游戏性价比分析 - 改进版】

分析样本：10,163款高质量付费游戏（好评率≥60%，评论≥50）

【改进的性价比得分公式】
Value Score = (好评率^1.5 × ln(游戏时长) × ln(内容分数)) / ln(总价格)

改进点：
  1. 质量门槛：要求好评率≥60%，评论数≥50（过滤低质量游戏）
  2. 好评率权重：使用1.5次方，更重视游戏质量
  3. 内容分数：降低DLC权重，增加游戏时长权重
  4. 归一化方法：使用百分位数，分数分布更均衡
  5. 最终分数：0-100分（百分位数排名）

【性价比分数统计】
平均性价比分数: 50.0分
中位数性价比分数: 50.0分
最高性价比分数: 100.0分
25分位数: 25.0分
75分位数: 75.0分

【每小时成本统计】
平均每小时成本: $3.15
中位数每小时成本: $1.90
最低每小时成本: $0.00
最高每小时成本: $83.07

【总拥有成本统计】
平均总拥有成本: $24.44
中位数总拥有成本: $11.49

【样本质量提升】
  - 平均好评率: 82.9%
  - 平均评论数: 6,207条
  - 平均游戏时长: 10.3小时


In [194]:
# 2. 可视化：价格 vs 游戏时长散点图

print("\n【价格 vs 游戏时长分析】\n")

# 创建散点图（采样避免过多数据点）
sample_size = min(5000, len(value_games))
value_sample = value_games.sample(sample_size)

fig26 = px.scatter(value_sample,
                   x='Price',
                   y='Playtime hours',
                   size='Value score',
                   color='Positive rate',
                   hover_data=['Name', 'Primary genre', 'Cost per hour', 'Total ownership cost'],
                   title='价格 vs 游戏时长 (气泡大小=性价比分数，颜色=好评率)',
                   labels={
                       'Price': '基础价格 ($)',
                       'Playtime hours': '平均游戏时长 (小时)',
                       'Value score': '性价比分数',
                       'Positive rate': '好评率'
                   },
                   color_continuous_scale='RdYlGn',
                   range_color=[0.5, 1.0],
                   log_y=True)  # 使用对数坐标

fig26.update_layout(height=600)
fig26.show()

# 按价格区间统计平均游戏时长和性价比
price_value_analysis = value_games.groupby('Price category').agg({
    'Playtime hours': 'median',
    'Cost per hour': 'median',
    'Value score': 'mean',
    'Total ownership cost': 'median',
    'AppID': 'count'
}).reset_index()

price_value_analysis.columns = ['Price category', 'Median playtime (hrs)', 
                                 'Median cost/hr', 'Avg value score', 
                                 'Median total cost', 'Game count']

# 按价格顺序排列
price_value_analysis['Price category'] = pd.Categorical(
    price_value_analysis['Price category'],
    categories=category_order,
    ordered=True
)
price_value_analysis = price_value_analysis.sort_values('Price category')

print("各价格区间的性价比对比:\n")
print(price_value_analysis.to_string(index=False))

print("\n【关键发现】")
# 找出性价比最高的价格区间
best_value_range = price_value_analysis.loc[price_value_analysis['Avg value score'].idxmax(), 'Price category']
print(f"- 性价比最高的价格区间: {best_value_range}")
print(f"  平均性价比分数: {price_value_analysis.loc[price_value_analysis['Avg value score'].idxmax(), 'Avg value score']:.1f}分")

# 找出每小时成本最低的价格区间
cheapest_per_hour = price_value_analysis.loc[price_value_analysis['Median cost/hr'].idxmin(), 'Price category']
print(f"\n- 每小时成本最低的价格区间: {cheapest_per_hour}")
print(f"  中位数每小时成本: ${price_value_analysis.loc[price_value_analysis['Median cost/hr'].idxmin(), 'Median cost/hr']:.2f}/小时")


【价格 vs 游戏时长分析】



各价格区间的性价比对比:

Price category  Median playtime (hrs)  Median cost/hr  Avg value score  Median total cost  Game count
          $0-5               2.983333        0.750628        56.778213             2.9900        2807
         $5-10               3.416667        2.040979        43.991628             9.9900        2506
        $10-20               4.533333        2.932518        46.390340            19.4870        3228
        $20-30               7.666667        3.177483        52.025623            29.9900         945
        $30-50              12.950000        2.930818        57.959144            49.9900         490
          $50+              14.400000        3.916649        60.258429            86.9855         187

【关键发现】
- 性价比最高的价格区间: $50+
  平均性价比分数: 60.3分

- 每小时成本最低的价格区间: $0-5
  中位数每小时成本: $0.75/小时


In [195]:
# 3. 改进的性价比排行榜：按价格区间分层展示

print("\n" + "="*80)
print("【改进版性价比排行榜】")
print("="*80 + "\n")

print("【改进说明】")
print("- 按价格区间分层排名，避免低价游戏霸榜")
print("- 所有游戏均通过质量筛选（好评率≥60%，评论≥50）")
print("- 更均衡地展示各价格区间的高性价比游戏\n")

# 为每个价格区间找出Top 10性价比游戏
price_ranges = ['$0-5', '$5-10', '$10-20', '$20-30', '$30-50', '$50+']

for price_range in price_ranges:
    range_games = value_games[value_games['Price category'] == price_range]
    
    if len(range_games) >= 5:  # 至少5款游戏才展示
        top_10 = range_games.nlargest(10, 'Value score')
        
        print("="*80)
        print(f"【{price_range}价格区间 Top 10性价比游戏】")
        print("="*80 + "\n")
        
        print(f"{'排名':<4} {'游戏名称':<38} {'价格':<8} {'时长':<8} {'好评率':<8} {'性价比':<6}")
        print("-" * 80)
        
        for i, (idx, row) in enumerate(top_10.iterrows(), 1):
            name = row['Name'][:35] + '...' if len(row['Name']) > 38 else row['Name']
            price = f"${row['Price']:.2f}"
            playtime = f"{row['Playtime hours']:.0f}h"
            rating = f"{row['Positive rate']:.1%}"
            score = f"{row['Value score']:.1f}"
            
            print(f"{i:2d}.  {name:<38} {price:<8} {playtime:<8} {rating:<8} {score:<6}")
        
        print(f"\n本区间统计：")
        print(f"  - 游戏总数: {len(range_games):,}款")
        print(f"  - 平均性价比: {range_games['Value score'].mean():.1f}分")
        print(f"  - 平均每小时成本: ${range_games['Cost per hour'].mean():.2f}")
        print(f"  - 平均游戏时长: {range_games['Playtime hours'].mean():.1f}小时\n")

# 可视化：各价格区间Top 3性价比游戏对比
print("="*80)
print("【各价格区间最佳性价比游戏对比】")
print("="*80 + "\n")

top_by_price_range = []

for price_range in price_ranges:
    range_games = value_games[value_games['Price category'] == price_range]
    if len(range_games) > 0:
        top_1 = range_games.nlargest(1, 'Value score').iloc[0]
        top_by_price_range.append({
            'Price range': price_range,
            'Game': top_1['Name'][:40],
            'Price': top_1['Price'],
            'Playtime hrs': top_1['Playtime hours'],
            'Positive rate': top_1['Positive rate'],
            'Value score': top_1['Value score'],
            'Cost/hr': top_1['Cost per hour']
        })

top_comparison_df = pd.DataFrame(top_by_price_range)

if len(top_comparison_df) > 0:
    print(top_comparison_df.to_string(index=False))
    
    # 可视化：对比图
    fig27 = px.bar(top_comparison_df,
                   x='Price range',
                   y='Value score',
                   color='Positive rate',
                   hover_data=['Game', 'Price', 'Playtime hrs', 'Cost/hr'],
                   title='各价格区间最佳性价比游戏对比',
                   labels={
                       'Price range': '价格区间',
                       'Value score': '性价比分数',
                       'Positive rate': '好评率'
                   },
                   text='Value score',
                   color_continuous_scale='RdYlGn',
                   range_color=[0.6, 1.0])
    
    fig27.update_traces(texttemplate='%{text:.1f}', textposition='outside')
    fig27.update_layout(height=500)
    fig27.show()

# 补充：总体Top 20（跨区间）
print("\n" + "="*80)
print("【跨价格区间 总体Top 20性价比游戏】")
print("="*80 + "\n")

overall_top_20 = value_games.nlargest(20, 'Value score')[
    ['Name', 'Price', 'Price category', 'Primary genre', 'Playtime hours', 
     'Cost per hour', 'Positive rate', 'Total reviews', 'Value score']
].copy()

print(f"{'排名':<4} {'游戏名称':<35} {'价格区间':<10} {'价格':<8} {'时长':<8} {'性价比':<6}")
print("-" * 85)

for i, (idx, row) in enumerate(overall_top_20.iterrows(), 1):
    name = row['Name'][:32] + '...' if len(row['Name']) > 35 else row['Name']
    price_range = row['Price category']
    price = f"${row['Price']:.2f}"
    playtime = f"{row['Playtime hours']:.0f}h"
    score = f"{row['Value score']:.1f}"
    
    print(f"{i:2d}.  {name:<35} {price_range:<10} {price:<8} {playtime:<8} {score:<6}")

print(f"\n【Top 20游戏统计】")
print(f"平均价格: ${overall_top_20['Price'].mean():.2f}")
print(f"平均游戏时长: {overall_top_20['Playtime hours'].mean():.0f}小时")
print(f"平均每小时成本: ${overall_top_20['Cost per hour'].mean():.2f}")
print(f"平均好评率: {overall_top_20['Positive rate'].mean():.2%}")
print(f"平均评论数: {overall_top_20['Total reviews'].mean():,.0f}条")

print(f"\n价格区间分布:")
for cat in overall_top_20['Price category'].value_counts().head(5).items():
    print(f"  - {cat[0]}: {cat[1]}款")

print(f"\n类型分布:")
for genre in overall_top_20['Primary genre'].value_counts().head(5).items():
    print(f"  - {genre[0]}: {genre[1]}款")


【改进版性价比排行榜】

【改进说明】
- 按价格区间分层排名，避免低价游戏霸榜
- 所有游戏均通过质量筛选（好评率≥60%，评论≥50）
- 更均衡地展示各价格区间的高性价比游戏

【$0-5价格区间 Top 10性价比游戏】

排名   游戏名称                                   价格       时长       好评率      性价比   
--------------------------------------------------------------------------------
 1.  Russian Life Simulator                 $0.49    59h      89.4%    100.0 
 2.  Ninja Stealth                          $0.99    36h      68.9%    100.0 
 3.  Zup! F                                 $0.99    17h      97.4%    100.0 
 4.  Hentai Memory                          $0.59    3h       90.1%    100.0 
 5.  RUSSIAPHOBIA                           $0.49    31h      70.7%    100.0 
 6.  Oik 3                                  $0.74    4h       88.0%    100.0 
 7.  Ninja Stealth 3                        $0.49    3h       79.6%    99.9  
 8.  #CuteSnake 2                           $0.99    69h      76.7%    99.9  
 9.  Mountain                               $0.99    49h      88.4%    99.9  
10.  #monstercakes    


【跨价格区间 总体Top 20性价比游戏】

排名   游戏名称                                价格区间       价格       时长       性价比   
-------------------------------------------------------------------------------------
 1.  Russian Life Simulator              $0-5       $0.49    59h      100.0 
 2.  Ninja Stealth                       $0-5       $0.99    36h      100.0 
 3.  Zup! F                              $0-5       $0.99    17h      100.0 
 4.  Hentai Memory                       $0-5       $0.59    3h       100.0 
 5.  RUSSIAPHOBIA                        $0-5       $0.49    31h      100.0 
 6.  Oik 3                               $0-5       $0.74    4h       100.0 
 7.  Ninja Stealth 3                     $0-5       $0.49    3h       99.9  
 8.  #CuteSnake 2                        $0-5       $0.99    69h      99.9  
 9.  Mountain                            $0-5       $0.99    49h      99.9  
10.  #monstercakes                       $0-5       $0.99    33h      99.9  
11.  Rock 'N' Roll Defense               $0

In [196]:
# 4. 每小时成本分布分析

print("\n" + "="*80)
print("【每小时成本分布分析】")
print("="*80 + "\n")

# 创建每小时成本分组
def cost_per_hour_category(cost):
    if cost < 0.5:
        return '<$0.5/小时'
    elif cost < 1:
        return '$0.5-1/小时'
    elif cost < 2:
        return '$1-2/小时'
    elif cost < 5:
        return '$2-5/小时'
    else:
        return '$5+/小时'

value_games['Cost per hour category'] = value_games['Cost per hour'].apply(cost_per_hour_category)

cost_dist = value_games['Cost per hour category'].value_counts().sort_index()
cost_order = ['<$0.5/小时', '$0.5-1/小时', '$1-2/小时', '$2-5/小时', '$5+/小时']

print("每小时成本分布:\n")
for cat in cost_order:
    if cat in cost_dist.index:
        count = cost_dist[cat]
        pct = count / len(value_games) * 100
        print(f"  {cat:<15}: {count:>6,}款 ({pct:>5.1f}%)")

# 可视化：每小时成本分布
fig28 = px.histogram(value_games[value_games['Cost per hour'] < 10],  # 排除极端值
                     x='Cost per hour',
                     nbins=50,
                     title='每小时成本分布（<$10/小时）',
                     labels={'Cost per hour': '每小时成本 ($)', 'count': '游戏数量'},
                     color_discrete_sequence=['skyblue'])

fig28.add_vline(x=value_games['Cost per hour'].median(), 
                line_dash="dash", line_color="red",
                annotation_text=f"中位数: ${value_games['Cost per hour'].median():.2f}/hr")

fig28.update_layout(height=400)
fig28.show()

# 创建每小时成本 vs 好评率散点图
fig29 = px.scatter(value_games[value_games['Cost per hour'] < 5].sample(min(3000, len(value_games))),
                   x='Cost per hour',
                   y='Positive rate',
                   size='Playtime hours',
                   color='Price category',
                   hover_data=['Name', 'Price', 'Playtime hours'],
                   title='每小时成本 vs 好评率 (气泡大小=游戏时长)',
                   labels={
                       'Cost per hour': '每小时成本 ($)',
                       'Positive rate': '好评率',
                       'Playtime hours': '游戏时长（小时）',
                       'Price category': '价格区间'
                   },
                   category_orders={'Price category': category_order})

fig29.update_layout(height=600)
fig29.show()

print("\n【每小时成本洞察】")
# 找出每小时成本<$0.5的游戏（超高性价比）
ultra_cheap = value_games[value_games['Cost per hour'] < 0.5]
print(f"\n超高性价比游戏（<$0.5/小时）: {len(ultra_cheap):,}款")
print(f"  占分析样本的比例: {len(ultra_cheap)/len(value_games)*100:.1f}%")
print(f"  这些游戏的平均时长: {ultra_cheap['Playtime hours'].mean():.0f}小时")
print(f"  这些游戏的平均价格: ${ultra_cheap['Price'].mean():.2f}")
print(f"\n  超高性价比游戏Top 5类型:")
for genre, count in ultra_cheap['Primary genre'].value_counts().head(5).items():
    pct = count / len(ultra_cheap) * 100
    print(f"    - {genre}: {count}款 ({pct:.1f}%)")


【每小时成本分布分析】

每小时成本分布:

  <$0.5/小时       :  1,433款 ( 14.1%)
  $0.5-1/小时      :  1,514款 ( 14.9%)
  $1-2/小时        :  2,316款 ( 22.8%)
  $2-5/小时        :  3,079款 ( 30.3%)
  $5+/小时         :  1,821款 ( 17.9%)



【每小时成本洞察】

超高性价比游戏（<$0.5/小时）: 1,433款
  占分析样本的比例: 14.1%
  这些游戏的平均时长: 34小时
  这些游戏的平均价格: $6.17

  超高性价比游戏Top 5类型:
    - Action: 540款 (37.7%)
    - Casual: 289款 (20.2%)
    - Adventure: 260款 (18.1%)
    - Indie: 135款 (9.4%)
    - Strategy: 57款 (4.0%)


In [197]:
# 5. 按游戏类型推荐性价比之王

print("\n" + "="*80)
print("【各类型性价比之王推荐】")
print("="*80 + "\n")

# 为每个主要游戏类型找出性价比最高的10款游戏
genre_value_kings = []

for genre in top_6_genres:
    genre_games = value_games[value_games['Primary genre'] == genre]
    
    if len(genre_games) >= 10:
        # 选出该类型性价比最高的10款游戏
        top_10 = genre_games.nlargest(10, 'Value score')
        
        for idx, row in top_10.iterrows():
            genre_value_kings.append({
                'Genre': genre,
                'Rank': len(genre_value_kings) % 10 + 1,
                'Name': row['Name'],
                'Price': row['Price'],
                'Playtime hrs': row['Playtime hours'],
                'Cost/hr': row['Cost per hour'],
                'Total cost': row['Total ownership cost'],
                'Positive rate': row['Positive rate'],
                'DLC count': row['DLC count'],
                'Value score': row['Value score']
            })

genre_value_df = pd.DataFrame(genre_value_kings)

# 为每个类型打印推荐列表
for genre in top_6_genres:
    genre_recommendations = genre_value_df[genre_value_df['Genre'] == genre]
    
    if len(genre_recommendations) > 0:
        print(f"\n【{genre}】性价比Top 10\n")
        print(f"{'#':<3} {'游戏名称':<35} {'价格':<8} {'时长':<8} {'性价比':<6}")
        print("-" * 70)
        
        for idx, row in genre_recommendations.head(10).iterrows():
            name = row['Name'][:32] + '...' if len(row['Name']) > 35 else row['Name']
            rank = row['Rank']
            price = f"${row['Price']:.2f}"
            playtime = f"{row['Playtime hrs']:.0f}h"
            value = f"{row['Value score']:.1f}"
            
            print(f"{rank:<3} {name:<35} {price:<8} {playtime:<8} {value:<6}")

# 创建各类型性价比对比图
genre_value_summary = value_games.groupby('Primary genre').agg({
    'Value score': 'mean',
    'Cost per hour': 'median',
    'Playtime hours': 'median',
    'Price': 'median',
    'AppID': 'count'
}).reset_index()

genre_value_summary.columns = ['Genre', 'Avg value score', 'Median cost/hr', 
                                'Median playtime', 'Median price', 'Game count']
genre_value_summary = genre_value_summary.sort_values('Avg value score', ascending=False)

print("\n" + "="*80)
print("\n【各类型性价比对比统计】\n")
print(genre_value_summary[genre_value_summary['Genre'].isin(top_6_genres)].to_string(index=False))

# 可视化：各类型平均性价比分数
fig30 = px.bar(genre_value_summary[genre_value_summary['Genre'].isin(top_6_genres)],
               x='Genre',
               y='Avg value score',
               color='Median cost/hr',
               title='各游戏类型平均性价比分数',
               labels={'Genre': '游戏类型', 'Avg value score': '平均性价比分数', 'Median cost/hr': '中位数每小时成本'},
               text='Avg value score',
               color_continuous_scale='RdYlGn_r')

fig30.update_traces(texttemplate='%{text:.1f}', textposition='outside')
fig30.update_layout(height=500)
fig30.show()

print("\n【类型性价比洞察】")
best_value_genre = genre_value_summary[genre_value_summary['Genre'].isin(top_6_genres)].iloc[0]
print(f"\n性价比最高的类型: {best_value_genre['Genre']}")
print(f"  平均性价比分数: {best_value_genre['Avg value score']:.1f}分")
print(f"  中位数每小时成本: ${best_value_genre['Median cost/hr']:.2f}")
print(f"  中位数游戏时长: {best_value_genre['Median playtime']:.0f}小时")


【各类型性价比之王推荐】


【Indie】性价比Top 10

#   游戏名称                                价格       时长       性价比   
----------------------------------------------------------------------
1   Oh My Gore!                         $0.49    6h       99.8  
2   Super Switch                        $0.51    8h       99.6  
3   100% Orange Juice                   $1.74    31h      99.5  
4   FTL: Faster Than Light              $2.49    30h      99.5  
5   Bounty Train                        $0.99    16h      99.1  
6   Town of Salem                       $4.99    39h      98.8  
7   Garry's Mod                         $9.99    182h     98.7  
8   Hacknet                             $9.99    113h     98.5  
9   Doom & Destiny Advanced             $0.99    5h       98.5  
10  Euro Truck Simulator 2              $19.99   107h     98.3  

【Casual】性价比Top 10

#   游戏名称                                价格       时长       性价比   
----------------------------------------------------------------------
1   Ninja Stealth       


【类型性价比洞察】

性价比最高的类型: Simulation
  平均性价比分数: 54.7分
  中位数每小时成本: $1.68
  中位数游戏时长: 8小时


In [198]:
# 6. 任务3.1总结：性价比分析关键发现

print("\n" + "="*80)
print("【任务3.1 关键发现总结】")
print("="*80 + "\n")

print("1. 性价比得分系统:")
print(f"   - 分析样本: {len(value_games):,}款付费成功游戏")
print(f"   - 平均性价比分数: {value_games['Value score'].mean():.1f}/100分")
print(f"   - 公式权重: 好评率 × 时长 × 内容量 / 总成本")

print("\n2. 每小时成本发现:")
print(f"   - 中位数每小时成本: ${value_games['Cost per hour'].median():.2f}/小时")
ultra_cheap_pct = len(value_games[value_games['Cost per hour'] < 0.5]) / len(value_games) * 100
print(f"   - 超高性价比游戏(<$0.5/hr): {ultra_cheap_pct:.1f}%")

if len(price_value_analysis) > 0:
    best_price_range = price_value_analysis.loc[price_value_analysis['Avg value score'].idxmax()]
    print(f"\n3. 最佳性价比价格区间:")
    print(f"   - 价格区间: {best_price_range['Price category']}")
    print(f"   - 平均性价比分数: {best_price_range['Avg value score']:.1f}/100分")
    print(f"   - 中位数每小时成本: ${best_price_range['Median cost/hr']:.2f}")

if len(top_value_games) > 0:
    print(f"\n4. 性价比Top 50游戏特征:")
    print(f"   - 平均价格: ${top_value_games['Price'].mean():.2f}")
    print(f"   - 平均时长: {top_value_games['Playtime hours'].mean():.0f}小时")
    print(f"   - 平均每小时成本: ${top_value_games['Cost per hour'].mean():.2f}")
    print(f"   - 平均好评率: {top_value_games['Positive rate'].mean():.1%}")
    print(f"   - 主导类型: {top_value_games['Primary genre'].mode()[0]}")

if len(genre_value_summary) > 0:
    best_genre = genre_value_summary[genre_value_summary['Genre'].isin(top_6_genres)].iloc[0]
    print(f"\n5. 各类型性价比:")
    print(f"   - 性价比最高类型: {best_genre['Genre']}")
    print(f"   - 该类型平均分数: {best_genre['Avg value score']:.1f}/100分")
    print(f"   - 该类型中位数每小时成本: ${best_genre['Median cost/hr']:.2f}")

print("\n" + "="*80)
print("【给玩家的购买建议】")
print("="*80 + "\n")

print("基于性价比分析，玩家可以:")

print("\n✅ 如果追求最高性价比:")
if len(top_value_games) > 0:
    top_3 = top_value_games.head(3)
    for i, (idx, row) in enumerate(top_3.iterrows(), 1):
        print(f"   {i}. {row['Name'][:40]} (${row['Price']:.2f}, {row['Playtime hours']:.0f}小时, 性价比{row['Value score']:.1f}分)")

print("\n📊 如果按预算选择:")
if len(price_value_analysis) > 0:
    for idx, row in price_value_analysis.iterrows():
        if row['Game count'] >= 10:
            print(f"   - {row['Price category']}: 平均性价比{row['Avg value score']:.1f}分, 中位数{row['Median cost/hr']:.2f}$/小时")

print("\n🎯 如果按类型偏好:")
if len(genre_value_summary) > 0:
    for idx, row in genre_value_summary[genre_value_summary['Genre'].isin(top_6_genres)].head(3).iterrows():
        print(f"   - {row['Genre']}: 平均性价比{row['Avg value score']:.1f}分")

print("\n💡 性价比购买建议:")
print("   1. $10-20区间游戏通常性价比最高")
print("   2. 寻找游戏时长>50小时且DLC丰富的游戏")
print("   3. 避免单纯追求低价，关注时长和内容量")
print("   4. 参考性价比排行榜，在同类型中选择高分游戏")

print("\n" + "="*80)
print("注意：性价比不等于游戏质量，玩家应结合个人偏好和评价综合判断")
print("="*80)


【任务3.1 关键发现总结】

1. 性价比得分系统:
   - 分析样本: 10,163款付费成功游戏
   - 平均性价比分数: 50.0/100分
   - 公式权重: 好评率 × 时长 × 内容量 / 总成本

2. 每小时成本发现:
   - 中位数每小时成本: $1.90/小时
   - 超高性价比游戏(<$0.5/hr): 14.1%

3. 最佳性价比价格区间:
   - 价格区间: $50+
   - 平均性价比分数: 60.3/100分
   - 中位数每小时成本: $3.92

4. 性价比Top 50游戏特征:
   - 平均价格: $0.92
   - 平均时长: 18小时
   - 平均每小时成本: $0.12
   - 平均好评率: 81.7%
   - 主导类型: Casual

5. 各类型性价比:
   - 性价比最高类型: Simulation
   - 该类型平均分数: 54.7/100分
   - 该类型中位数每小时成本: $1.68

【给玩家的购买建议】

基于性价比分析，玩家可以:

✅ 如果追求最高性价比:
   1. Ninja Stealth ($0.99, 36小时, 性价比100.0分)
   2. Russian Life Simulator ($0.49, 59小时, 性价比97.8分)
   3. Ninja Stealth 3 ($0.49, 3小时, 性价比75.9分)

📊 如果按预算选择:
   - $0-5: 平均性价比56.8分, 中位数0.75$/小时
   - $5-10: 平均性价比44.0分, 中位数2.04$/小时
   - $10-20: 平均性价比46.4分, 中位数2.93$/小时
   - $20-30: 平均性价比52.0分, 中位数3.18$/小时
   - $30-50: 平均性价比58.0分, 中位数2.93$/小时
   - $50+: 平均性价比60.3分, 中位数3.92$/小时

🎯 如果按类型偏好:
   - Simulation: 平均性价比54.7分
   - Casual: 平均性价比52.9分
   - Strategy: 平均性价比50.8分

💡 性价比购买建议:
   1. $10-20区间游戏通常性价比最高
   2. 寻找游戏时长>50